## NOTE: the process is manual for now (grabbing data per year and saves it to csv) I will recode this to work per url dynamically when I have more time

In [175]:
import numpy as np
import pandas as pd
from bs4 import BeautifulSoup
import requests
import re
import dateutil.parser
import datetime

In [176]:
from IPython.core.display import display, HTML

In [177]:
#requesting movies for 2019
url = 'https://www.boxofficemojo.com/year/2019/?ref_=bo_yl_table_3'

In [178]:
response = requests.get(url)
page = response.text

In [179]:
soup = BeautifulSoup(page, "lxml")

In [180]:
table2019 = soup.find('table')

In [181]:
table2019

<table class="a-bordered a-horizontal-stripes a-size-base a-span12 mojo-body-table mojo-table-annotated mojo-body-table-compact"><tr><th class="a-text-right mojo-field-type-rank mojo-sort-column mojo-sortable-column a-nowrap"><a class="a-link-normal a-nowrap" href="?sort=rank&amp;ref_=bo_yld__resort#table" title="Rank"><span class="a-color-state">Rank</span><span class="a-letter-space"></span><span class="icon aok-relative"><i class="a-icon a-icon-collapse" role="presentation"></i></span></a></th><th class="a-text-left mojo-field-type-release mojo-cell-wide mojo-sortable-column a-nowrap"><span title="Release">Release</span>
</th><th class="a-text-left mojo-field-type-genre hidden mojo-sortable-column hidden a-nowrap"><span title="Genre">Genre</span>
</th><th class="a-text-right mojo-field-type-money hidden mojo-sortable-column hidden a-nowrap"><span title="Budget">Budget</span>
</th><th class="a-text-right mojo-field-type-duration hidden mojo-sortable-column hidden a-nowrap"><span titl

In [182]:
rows = [row for row in table2019.find_all('tr')]

In [183]:
rows[1].find_all('td')[1].find('a').get('href')
# same rows[1].find_all('td')[1].find('a')['href']

'/release/rl3059975681/?ref_=bo_yld_table_1'

In [184]:
rows[1].find_all('td', class_="a-text-left mojo-field-type-studio")[0].text

'Walt Disney Studios Motion Pictures\n\n'

In [185]:
rows[1].find_all('td')[1].find('a')

<a class="a-link-normal" href="/release/rl3059975681/?ref_=bo_yld_table_1">Avengers: Endgame</a>

In [186]:
movies2019 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2019[title] = [url, theaters, release_date, distributor]
    

In [187]:
movies2019

{'Avengers: Endgame': ['/release/rl3059975681/?ref_=bo_yld_table_1',
  '4,662',
  'Apr 26',
  'Walt Disney Studios Motion Pictures\n\n'],
 'The Lion King': ['/release/rl3321923073/?ref_=bo_yld_table_2',
  '4,802',
  'Jul 19',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Toy Story 4': ['/release/rl3798500865/?ref_=bo_yld_table_3',
  '4,575',
  'Jun 21',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Frozen II': ['/release/rl2424210945/?ref_=bo_yld_table_4',
  '4,440',
  'Nov 22',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Captain Marvel': ['/release/rl3009644033/?ref_=bo_yld_table_5',
  '4,310',
  'Mar 8',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Star Wars: Episode IX - The Rise of Skywalker': ['/release/rl3305145857/?ref_=bo_yld_table_6',
  '4,406',
  'Dec 20',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Spider-Man: Far from Home': ['/release/rl3791750657/?ref_=bo_yld_table_7',
  '4,634',
  'Jul 2',
  'Sony Pictures Entertainment (SPE)\n\n'],
 'Aladdin': ['/release/

In [188]:
movies2019_df = pd.DataFrame(movies2019).T

In [189]:
movies2019_df.head()

0      1       2  \
Avengers: Endgame  /release/rl3059975681/?ref_=bo_yld_table_1  4,662  Apr 26   
The Lion King      /release/rl3321923073/?ref_=bo_yld_table_2  4,802  Jul 19   
Toy Story 4        /release/rl3798500865/?ref_=bo_yld_table_3  4,575  Jun 21   
Frozen II          /release/rl2424210945/?ref_=bo_yld_table_4  4,440  Nov 22   
Captain Marvel     /release/rl3009644033/?ref_=bo_yld_table_5  4,310   Mar 8   

                                                         3  
Avengers: Endgame  Walt Disney Studios Motion Pictures\n\n  
The Lion King      Walt Disney Studios Motion Pictures\n\n  
Toy Story 4        Walt Disney Studios Motion Pictures\n\n  
Frozen II          Walt Disney Studios Motion Pictures\n\n  
Captain Marvel     Walt Disney Studios Motion Pictures\n\n

In [190]:
movies2019_df.columns = ['link', 'theaters', 'release_date', 'Distributor']

In [191]:
movies2019_df

link  \
Avengers: Endgame           /release/rl3059975681/?ref_=bo_yld_table_1   
The Lion King               /release/rl3321923073/?ref_=bo_yld_table_2   
Toy Story 4                 /release/rl3798500865/?ref_=bo_yld_table_3   
Frozen II                   /release/rl2424210945/?ref_=bo_yld_table_4   
Captain Marvel              /release/rl3009644033/?ref_=bo_yld_table_5   
...                                                                ...   
Welcome to Marwen         /release/rl2264958465/?ref_=bo_yld_table_196   
My People, My Country     /release/rl2433451521/?ref_=bo_yld_table_197   
Promare                   /release/rl3104540161/?ref_=bo_yld_table_198   
Super 30                  /release/rl4211639809/?ref_=bo_yld_table_199   
Faustina: Love and Mercy   /release/rl252413441/?ref_=bo_yld_table_200   

                         theaters release_date  \
Avengers: Endgame           4,662       Apr 26   
The Lion King               4,802       Jul 19   
Toy Story 4                 4,575       Jun 21   
Frozen II                   4,440       Nov 22   
Captain Marvel              4,310        Mar 8   
...                           ...          ...   
Welcome to Marwen           1,911       Dec 21   
My People, My Country          83        Oct 1   
Promare                       701       Sep 17   
Super 30                      317       Jul 12   
Faustina: Love and Mercy      810       Oct 28   

                                                      Distributor  
Avengers: Endgame         Walt Disney Studios Motion Pictures\n\n  
The Lion King             Walt Disney Studios Motion Pictures\n\n  
Toy Story 4               Walt Disney Studios Motion Pictures\n\n  
Frozen II                 Walt Disney Studios Motion Pictures\n\n  
Captain Marvel            Walt Disney Studios Motion Pictures\n\n  
...                                                           ...  
Welcome to Marwen                          Universal Pictures\n\n  
My People, My Country                                           -  
Promare                                                 GKIDS\n\n  
Super 30                                Reliance Big Pictures\n\n  
Faustina: Love and Mercy                        Fathom Events\n\n  

[200 rows x 4 columns]

In [192]:
movies2019_df['Distributor'].replace('\n', '', regex=True, inplace=True)

In [193]:
movies2019_df['release_year'] = 2019

In [194]:
def get_movie_info(soup, field_name):
    """
    Grab a value from Box Office Mojo HTML
    Takes a string attribute of a movie on the page and returns the string in
    the next sibling object (the value for that attribute) or None if nothing is found.
    """
    
    obj = soup.find(text=re.compile(field_name))
    
    if not obj: 
        return None
    
    next_element = obj.findNext()
    
    if next_element:
        return next_element.text 
    else:
        return None

In [195]:
def money_to_int(moneystring):
    if not moneystring:
        return None
    
    moneystring = moneystring.replace('$', '').replace(',', '')
    return int(moneystring)

def runtime_to_minutes(runtimestring):
    if not runtimestring:
        return None
    
    runtime = runtimestring.split()
    try:
        minutes = int(runtime[0])*60 + int(runtime[2])
        return minutes
    except:
        return None

def to_date(datestring):
    date = dateutil.parser.parse(datestring)
    return date

In [196]:
def get_movie_dict(link):
    """
    Collect data about the movie from boxofficemojo.com using BeautifulSoup 
    and store this information in a dictionary
    """
    
    home_url = 'https://www.boxofficemojo.com'
    
    #create a full url of the movie requested
    url = home_url + link
    
    #request html of the page and parse it
    response = requests.get(url)
    page = response.text
    soup = BeautifulSoup(page, "lxml")
    
    headers = ['movie_title', 'genres', 'runtime', 'rating', 'budget', 'dom_gross', 'int_gross']
    
    #get title
    title_string = soup.find('title').text
    title = title_string.split('-')[0].strip()
    
    #get genres 
    genres_string = get_movie_info(soup, 'Genres')
    genres_string.replace('\n', '')
    genres = ' '.join(genres_string.split())
    
    #get runtime
    runtime_string = get_movie_info(soup, 'Running Time')
    runtime = runtime_to_minutes(runtime_string)
    
    #get rating
    rating = get_movie_info(soup, 'MPAA')
    
    #get budget
    budget_string = get_movie_info(soup, 'Budget')
    budget = money_to_int(budget_string)
    
    #get dom gross
    dom_gross_string = soup.find(class_='a-section a-spacing-none mojo-performance-summary-table')\
    .find_all('span', class_='money')[0].text
    dom_gross = money_to_int(dom_gross_string)
    
    #get int gross
    int_gross_string = soup.find(class_='a-section a-spacing-none mojo-performance-summary-table')\
    .find_all('span', class_='money')[1].text
    int_gross = money_to_int(int_gross_string)    
    
    
    #create movie dictionary and return
    
    movie_dict = dict(zip(headers, [title, genres, runtime, rating, budget, dom_gross, int_gross]))
    
    
    return movie_dict

In [197]:
movies_page_info_list_2019 = []

In [198]:
for link in movies2019_df.link:
    movies_page_info_list_2019.append(get_movie_dict(link))

In [199]:
movies_page_info_list_2019

[{'movie_title': 'Avengers: Endgame',
  'genres': 'Action Adventure Drama Sci-Fi',
  'runtime': 181,
  'rating': 'PG-13',
  'budget': 356000000,
  'dom_gross': 858373000,
  'int_gross': 1939128328},
 {'movie_title': 'The Lion King',
  'genres': 'Adventure Animation Drama Family Musical',
  'runtime': 118,
  'rating': 'PG',
  'budget': 260000000,
  'dom_gross': 543638043,
  'int_gross': 1113305351},
 {'movie_title': 'Toy Story 4',
  'genres': 'Adventure Animation Comedy Family Fantasy',
  'runtime': 100,
  'rating': 'G',
  'budget': 200000000,
  'dom_gross': 434038008,
  'int_gross': 639356585},
 {'movie_title': 'Frozen II',
  'genres': 'Adventure Animation Comedy Family Fantasy Musical',
  'runtime': 103,
  'rating': 'PG',
  'budget': 150000000,
  'dom_gross': 477373578,
  'int_gross': 972653355},
 {'movie_title': 'Captain Marvel',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 123,
  'rating': 'PG-13',
  'budget': 160000000,
  'dom_gross': 426829839,
  'int_gross': 701444955},
 {

In [200]:
movieinfo2019_df = pd.DataFrame(movies_page_info_list_2019)

In [201]:
movieinfo2019_df.set_index('movie_title', inplace=True)

In [202]:
movieinfo2019_df

genres  \
movie_title                                                                   
Avengers: Endgame                             Action Adventure Drama Sci-Fi   
The Lion King                      Adventure Animation Drama Family Musical   
Toy Story 4                       Adventure Animation Comedy Family Fantasy   
Frozen II                 Adventure Animation Comedy Family Fantasy Musical   
Captain Marvel                                      Action Adventure Sci-Fi   
...                                                                     ...   
Welcome to Marwen                    Biography Comedy Drama Fantasy Romance   
My People, My Country                                         Drama History   
Promare                   Action Adventure Animation Comedy Drama Fantas...   
Super 30                                                    Biography Drama   
Faustina: Love and Mercy                             Biography Drama Family   

                          runtime rating       budget  dom_gross   int_gross  
movie_title                                                                   
Avengers: Endgame           181.0  PG-13  356000000.0  858373000  1939128328  
The Lion King               118.0     PG  260000000.0  543638043  1113305351  
Toy Story 4                 100.0      G  200000000.0  434038008   639356585  
Frozen II                   103.0     PG  150000000.0  477373578   972653355  
Captain Marvel              123.0  PG-13  160000000.0  426829839   701444955  
...                           ...    ...          ...        ...         ...  
Welcome to Marwen           116.0  PG-13          NaN   10763520     2297971  
My People, My Country       154.0   None          NaN    2356683   447708310  
Promare                     111.0  PG-13          NaN    2313596     7153740  
Super 30                    154.0   None          NaN    2269878    22431759  
Faustina: Love and Mercy    107.0   None          NaN    2243180     1255707  

[200 rows x 6 columns]

In [203]:
movies2019_df = movies2019_df.merge(movieinfo2019_df, left_index=True, right_index=True)

In [204]:
movies2019_df

link  \
21 Bridges                            /release/rl2886174209/?ref_=bo_yld_table_86   
47 Meters Down: Uncaged              /release/rl1526892033/?ref_=bo_yld_table_100   
A Beautiful Day in the Neighborhood   /release/rl2651096577/?ref_=bo_yld_table_49   
A Dog's Journey                       /release/rl3036972545/?ref_=bo_yld_table_96   
A Dog's Way Home                      /release/rl3238364673/?ref_=bo_yld_table_65   
...                                                                           ...   
What Men Want                         /release/rl3221390849/?ref_=bo_yld_table_54   
Where'd You Go, Bernadette           /release/rl2567276033/?ref_=bo_yld_table_138   
Wonder Park                           /release/rl2575074817/?ref_=bo_yld_table_61   
Yesterday                             /release/rl1392805377/?ref_=bo_yld_table_38   
Zombieland: Double Tap                 /release/rl201819649/?ref_=bo_yld_table_40   

                                    theaters release_date  \
21 Bridges                             2,665       Nov 22   
47 Meters Down: Uncaged                2,883       Aug 16   
A Beautiful Day in the Neighborhood    3,491       Nov 22   
A Dog's Journey                        3,279       May 17   
A Dog's Way Home                       3,090       Jan 11   
...                                      ...          ...   
What Men Want                          2,912        Feb 8   
Where'd You Go, Bernadette             2,404       Aug 16   
Wonder Park                            3,838       Mar 15   
Yesterday                              2,755       Jun 28   
Zombieland: Double Tap                 3,468       Oct 18   

                                                               Distributor  \
21 Bridges                                               STX Entertainment   
47 Meters Down: Uncaged              Entertainment Studios Motion Pictures   
A Beautiful Day in the Neighborhood      Sony Pictures Entertainment (SPE)   
A Dog's Journey                                         Universal Pictures   
A Dog's Way Home                         Sony Pictures Entertainment (SPE)   
...                                                                    ...   
What Men Want                                           Paramount Pictures   
Where'd You Go, Bernadette                        United Artists Releasing   
Wonder Park                                             Paramount Pictures   
Yesterday                                               Universal Pictures   
Zombieland: Double Tap                   Sony Pictures Entertainment (SPE)   

                                     release_year  \
21 Bridges                                   2019   
47 Meters Down: Uncaged                      2019   
A Beautiful Day in the Neighborhood          2019   
A Dog's Journey                              2019   
A Dog's Way Home                             2019   
...                                           ...   
What Men Want                                2019   
Where'd You Go, Bernadette                   2019   
Wonder Park                                  2019   
Yesterday                                    2019   
Zombieland: Double Tap                       2019   

                                                                              genres  \
21 Bridges                                                     Action Crime Thriller   
47 Meters Down: Uncaged                              Adventure Drama Horror Thriller   
A Beautiful Day in the Neighborhood                                  Biography Drama   
A Dog's Journey                                Adventure Comedy Drama Family Fantasy   
A Dog's Way Home                                              Adventure Drama Family   
...                                                                              ...   
What Men Want                                                 Comedy Fantasy Romance   
Where'd You Go, Bernadette                   

In [205]:
movies2019_df.describe()

release_year     runtime        budget     dom_gross     int_gross
count         192.0  187.000000  1.200000e+02  1.920000e+02  1.920000e+02
mean         2019.0  113.267380  5.789250e+07  6.376170e+07  1.120297e+08
std             0.0   19.487331  6.345886e+07  1.063401e+08  2.325632e+08
min          2019.0   76.000000  5.000000e+06  2.243180e+06  4.197000e+03
25%          2019.0   99.500000  1.475000e+07  7.572041e+06  6.160865e+06
50%          2019.0  109.000000  3.250000e+07  2.729657e+07  2.372036e+07
75%          2019.0  123.500000  8.250000e+07  6.896792e+07  8.911666e+07
max          2019.0  181.000000  3.560000e+08  8.583730e+08  1.939128e+09

In [206]:
movies2019_df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 192 entries, 21 Bridges to Zombieland: Double Tap
Data columns (total 11 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   link          192 non-null    object 
 1   theaters      192 non-null    object 
 2   release_date  192 non-null    object 
 3   Distributor   192 non-null    object 
 4   release_year  192 non-null    int64  
 5   genres        192 non-null    object 
 6   runtime       187 non-null    float64
 7   rating        175 non-null    object 
 8   budget        120 non-null    float64
 9   dom_gross     192 non-null    int64  
 10  int_gross     192 non-null    int64  
dtypes: float64(2), int64(3), object(6)
memory usage: 18.0+ KB


In [207]:
movies2019_df.rating.value_counts()

R            67
PG-13        64
PG           38
G             4
Not Rated     2
Name: rating, dtype: int64

In [208]:
movies2019_df.isna().sum()

link             0
theaters         0
release_date     0
Distributor      0
release_year     0
genres           0
runtime          5
rating          17
budget          72
dom_gross        0
int_gross        0
dtype: int64

In [209]:
movies2019_df.to_csv('movies_2019')

In [210]:
movies2019_df.count()

link            192
theaters        192
release_date    192
Distributor     192
release_year    192
genres          192
runtime         187
rating          175
budget          120
dom_gross       192
int_gross       192
dtype: int64

In [211]:
movies2019_df.shape

(192, 11)

In [212]:
#requesting movies for 2018
url2 = 'https://www.boxofficemojo.com/year/2018/?ref_=bo_yl_table_4'

In [213]:
response = requests.get(url2)
page = response.text

In [214]:
soup = BeautifulSoup(page, 'lxml')

In [215]:
soup

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo"><head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta charset="utf-8"/>
<title dir="ltr">Domestic Box Office For 2018 - Box Office Mojo</title><meta content="Domestic Box Office For 2018" name="title"/>
<meta content="Box Office Mojo" property="og:site_name"/>
<meta content="https://m.media-amazon.com/images/G/01/boxofficemojo/logo/mojo-logo-bg.png" property="og:image"/>
<meta content="telephone=no" name="format-detection"/>
<link href="https://m.media-amazon.com/images/G/01/boxofficemojo/v2/favicon._CB448965889_.ico" rel="icon" type="image/x-icon"/>
<link href="https://www.boxofficemojo.com/year/2018/" rel="canonical"/>
<link href="https://images-na.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41DAFIecsVL.css,51IB+wfP8qL.css,01ZfXnjPmmL.css,01oDR3IULNL.css,01Vctty9pOL.css,31ZcpBfSgNL.css,01XPHJk60-L

In [216]:
table2018 = soup.find('table')

In [217]:
table2018

<table class="a-bordered a-horizontal-stripes a-size-base a-span12 mojo-body-table mojo-table-annotated mojo-body-table-compact"><tr><th class="a-text-right mojo-field-type-rank mojo-sort-column mojo-sortable-column a-nowrap"><a class="a-link-normal a-nowrap" href="?sort=rank&amp;ref_=bo_yld__resort#table" title="Rank"><span class="a-color-state">Rank</span><span class="a-letter-space"></span><span class="icon aok-relative"><i class="a-icon a-icon-collapse" role="presentation"></i></span></a></th><th class="a-text-left mojo-field-type-release mojo-cell-wide mojo-sortable-column a-nowrap"><span title="Release">Release</span>
</th><th class="a-text-left mojo-field-type-genre hidden mojo-sortable-column hidden a-nowrap"><span title="Genre">Genre</span>
</th><th class="a-text-right mojo-field-type-money hidden mojo-sortable-column hidden a-nowrap"><span title="Budget">Budget</span>
</th><th class="a-text-right mojo-field-type-duration hidden mojo-sortable-column hidden a-nowrap"><span titl

In [218]:
rows = [row for row in table2018.find_all('tr')]

In [219]:
rows

[<tr><th class="a-text-right mojo-field-type-rank mojo-sort-column mojo-sortable-column a-nowrap"><a class="a-link-normal a-nowrap" href="?sort=rank&amp;ref_=bo_yld__resort#table" title="Rank"><span class="a-color-state">Rank</span><span class="a-letter-space"></span><span class="icon aok-relative"><i class="a-icon a-icon-collapse" role="presentation"></i></span></a></th><th class="a-text-left mojo-field-type-release mojo-cell-wide mojo-sortable-column a-nowrap"><span title="Release">Release</span>
 </th><th class="a-text-left mojo-field-type-genre hidden mojo-sortable-column hidden a-nowrap"><span title="Genre">Genre</span>
 </th><th class="a-text-right mojo-field-type-money hidden mojo-sortable-column hidden a-nowrap"><span title="Budget">Budget</span>
 </th><th class="a-text-right mojo-field-type-duration hidden mojo-sortable-column hidden a-nowrap"><span title="Running Time">Running Time</span>
 </th><th class="a-text-right mojo-field-type-money mojo-sortable-column mojo-estimatabl

In [220]:
movies2018 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2018[title] = [url, theaters, release_date, distributor]

In [221]:
movies2018

{'Black Panther': ['/release/rl2992866817/?ref_=bo_yld_table_1',
  '4,084',
  'Feb 16',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Avengers: Infinity War': ['/release/rl3043198465/?ref_=bo_yld_table_2',
  '4,474',
  'Apr 27',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Incredibles 2': ['/release/rl2071758337/?ref_=bo_yld_table_3',
  '4,410',
  'Jun 15',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Jurassic World: Fallen Kingdom': ['/release/rl1602061825/?ref_=bo_yld_table_4',
  '4,485',
  'Jun 22',
  'Universal Pictures\n\n'],
 'Deadpool 2': ['/release/rl2488436225/?ref_=bo_yld_table_5',
  '4,349',
  'May 18',
  'Twentieth Century Fox\n\n'],
 'The Grinch': ['/release/rl3075966465/?ref_=bo_yld_table_6',
  '4,141',
  'Nov 9',
  'Universal Pictures\n\n'],
 'Jumanji: Welcome to the Jungle': ['/release/rl3095234049/?ref_=bo_yld_table_7',
  '3,849',
  'Dec 20',
  'Sony Pictures Entertainment (SPE)\n\n'],
 'Mission: Impossible - Fallout': ['/release/rl2449573377/?ref_=bo_yld_table

In [222]:
movies2018_df = pd.DataFrame(movies2018).T

In [223]:
movies2018_df

0  \
Black Panther                     /release/rl2992866817/?ref_=bo_yld_table_1   
Avengers: Infinity War            /release/rl3043198465/?ref_=bo_yld_table_2   
Incredibles 2                     /release/rl2071758337/?ref_=bo_yld_table_3   
Jurassic World: Fallen Kingdom    /release/rl1602061825/?ref_=bo_yld_table_4   
Deadpool 2                        /release/rl2488436225/?ref_=bo_yld_table_5   
...                                                                      ...   
The Disaster Artist             /release/rl1979942401/?ref_=bo_yld_table_196   
2001: A Space Odyssey           /release/rl2214888961/?ref_=bo_yld_table_197   
2.0                             /release/rl1644594689/?ref_=bo_yld_table_198   
The Leisure Seeker              /release/rl2164491777/?ref_=bo_yld_table_199   
The Sisters Brothers            /release/rl1376224769/?ref_=bo_yld_table_200   

                                    1       2  \
Black Panther                   4,084  Feb 16   
Avengers: Infinity War          4,474  Apr 27   
Incredibles 2                   4,410  Jun 15   
Jurassic World: Fallen Kingdom  4,485  Jun 22   
Deadpool 2                      4,349  May 18   
...                               ...     ...   
The Disaster Artist             1,010   Dec 1   
2001: A Space Odyssey              13  May 18   
2.0                               314  Nov 30   
The Leisure Seeker                353  Dec 15   
The Sisters Brothers            1,141  Sep 21   

                                                                      3  
Black Panther                   Walt Disney Studios Motion Pictures\n\n  
Avengers: Infinity War          Walt Disney Studios Motion Pictures\n\n  
Incredibles 2                   Walt Disney Studios Motion Pictures\n\n  
Jurassic World: Fallen Kingdom                   Universal Pictures\n\n  
Deadpool 2                                    Twentieth Century Fox\n\n  
...                                                                 ...  
The Disaster Artist                                             A24\n\n  
2001: A Space Odyssey                                  Warner Bros.\n\n  
2.0                                                                   -  
The Leisure Seeker                           Sony Pictures Classics\n\n  
The Sisters Brothers                             Annapurna Pictures\n\n  

[200 rows x 4 columns]

In [224]:
movies2018_df.columns = ['link', 'theaters', 'release_date', 'Distributor']

In [225]:
movies2018_df['Distributor'].replace('\n', '', regex=True, inplace=True)

In [226]:
movies2018_df['release_year'] = 2018

In [227]:
movies_page_info_list_2018 = []

In [228]:
for link in movies2018_df.link:
    movies_page_info_list_2018.append(get_movie_dict(link))

In [229]:
movies_page_info_list_2018

[{'movie_title': 'Black Panther',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 134,
  'rating': 'PG-13',
  'budget': None,
  'dom_gross': 700059566,
  'int_gross': 646853595},
 {'movie_title': 'Avengers: Infinity War',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 149,
  'rating': 'PG-13',
  'budget': None,
  'dom_gross': 678815482,
  'int_gross': 1369544272},
 {'movie_title': 'Incredibles 2',
  'genres': 'Action Adventure Animation Comedy Family Sci-Fi',
  'runtime': 118,
  'rating': 'PG',
  'budget': None,
  'dom_gross': 608581744,
  'int_gross': 634223615},
 {'movie_title': 'Jurassic World: Fallen Kingdom',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 128,
  'rating': 'PG-13',
  'budget': 170000000,
  'dom_gross': 417719760,
  'int_gross': 890748184},
 {'movie_title': 'Deadpool 2',
  'genres': 'Action Adventure Comedy Sci-Fi',
  'runtime': 119,
  'rating': 'R',
  'budget': 110000000,
  'dom_gross': 318491426,
  'int_gross': 416055185},
 {'movie_title': 'The Grinc

In [230]:
movieinfo2018_df = pd.DataFrame(movies_page_info_list_2018)

In [231]:
movieinfo2018_df.set_index('movie_title', inplace=True)

In [232]:
movieinfo2018_df

genres  \
movie_title                                                                       
Black Panther                                           Action Adventure Sci-Fi   
Avengers: Infinity War                                  Action Adventure Sci-Fi   
Incredibles 2                   Action Adventure Animation Comedy Family Sci-Fi   
Jurassic World: Fallen Kingdom                          Action Adventure Sci-Fi   
Deadpool 2                                       Action Adventure Comedy Sci-Fi   
...                                                                         ...   
The Disaster Artist                                      Biography Comedy Drama   
2001: A Space Odyssey 2018 Re                                  Adventure Sci-Fi   
2.0                                                               Action Sci-Fi   
The Leisure Seeker                               Adventure Comedy Drama Romance   
The Sisters Brothers                                        Crime Drama Western   

                                runtime rating       budget  dom_gross  \
movie_title                                                              
Black Panther                     134.0  PG-13          NaN  700059566   
Avengers: Infinity War            149.0  PG-13          NaN  678815482   
Incredibles 2                     118.0     PG          NaN  608581744   
Jurassic World: Fallen Kingdom    128.0  PG-13  170000000.0  417719760   
Deadpool 2                        119.0      R  110000000.0  318491426   
...                                 ...    ...          ...        ...   
The Disaster Artist               104.0      R          NaN   21120616   
2001: A Space Odyssey 2018 Re     149.0   None   12000000.0    3236321   
2.0                               148.0   None          NaN    4152000   
The Leisure Seeker                112.0      R          NaN    3226443   
The Sisters Brothers              122.0      R          NaN    3143056   

                                 int_gross  
movie_title                                 
Black Panther                    646853595  
Avengers: Infinity War          1369544272  
Incredibles 2                    634223615  
Jurassic World: Fallen Kingdom   890748184  
Deadpool 2                       416055185  
...                                    ...  
The Disaster Artist                8700000  
2001: A Space Odyssey 2018 Re       848261  
2.0                               32793969  
The Leisure Seeker                 7245737  
The Sisters Brothers              10000000  

[200 rows x 6 columns]

In [233]:
movieinfo2018_df.isna().sum()

genres        0
runtime       5
rating        6
budget       97
dom_gross     0
int_gross     0
dtype: int64

In [234]:
movies2018_df = movies2018_df.merge(movieinfo2018_df, left_index=True, right_index=True)

In [235]:
movies2018_df

link  \
Black Panther                     /release/rl2992866817/?ref_=bo_yld_table_1   
Avengers: Infinity War            /release/rl3043198465/?ref_=bo_yld_table_2   
Incredibles 2                     /release/rl2071758337/?ref_=bo_yld_table_3   
Jurassic World: Fallen Kingdom    /release/rl1602061825/?ref_=bo_yld_table_4   
Deadpool 2                        /release/rl2488436225/?ref_=bo_yld_table_5   
...                                                                      ...   
7 Days in Entebbe               /release/rl2298512897/?ref_=bo_yld_table_195   
The Disaster Artist             /release/rl1979942401/?ref_=bo_yld_table_196   
2.0                             /release/rl1644594689/?ref_=bo_yld_table_198   
The Leisure Seeker              /release/rl2164491777/?ref_=bo_yld_table_199   
The Sisters Brothers            /release/rl1376224769/?ref_=bo_yld_table_200   

                               theaters release_date  \
Black Panther                     4,084       Feb 16   
Avengers: Infinity War            4,474       Apr 27   
Incredibles 2                     4,410       Jun 15   
Jurassic World: Fallen Kingdom    4,485       Jun 22   
Deadpool 2                        4,349       May 18   
...                                 ...          ...   
7 Days in Entebbe                   838       Mar 16   
The Disaster Artist               1,010        Dec 1   
2.0                                 314       Nov 30   
The Leisure Seeker                  353       Dec 15   
The Sisters Brothers              1,141       Sep 21   

                                                        Distributor  \
Black Panther                   Walt Disney Studios Motion Pictures   
Avengers: Infinity War          Walt Disney Studios Motion Pictures   
Incredibles 2                   Walt Disney Studios Motion Pictures   
Jurassic World: Fallen Kingdom                   Universal Pictures   
Deadpool 2                                    Twentieth Century Fox   
...                                                             ...   
7 Days in Entebbe                                    Focus Features   
The Disaster Artist                                             A24   
2.0                                                               -   
The Leisure Seeker                           Sony Pictures Classics   
The Sisters Brothers                             Annapurna Pictures   

                                release_year  \
Black Panther                           2018   
Avengers: Infinity War                  2018   
Incredibles 2                           2018   
Jurassic World: Fallen Kingdom          2018   
Deadpool 2                              2018   
...                                      ...   
7 Days in Entebbe                       2018   
The Disaster Artist                     2018   
2.0                                     2018   
The Leisure Seeker                      2018   
The Sisters Brothers                    2018   

                                                                         genres  \
Black Panther                                           Action Adventure Sci-Fi   
Avengers: Infinity War                                  Action Adventure Sci-Fi   
Incredibles 2                   Action Adventure Animation Comedy Family Sci-Fi   
Jurassic World: Fallen Kingdom                          Action Adventure Sci-Fi   
Deadpool 2                                       Action Adventure Comedy Sci-Fi   
...                                                                         ...   
7 Days in Entebbe                                 Action Drama History Thriller   
The Disaster Artist                                      Biography Comedy Drama   
2.0                                                               Action Sci-Fi   
The Leisure Seeker                               Adventure Comedy Drama Romance   
The Sisters Brothers                                        Crime Drama Western   

           

In [236]:
movies2018_df.to_csv('movies_2018')

In [237]:
#requesting movies for 2017
url3 = 'https://www.boxofficemojo.com/year/2017/?ref_=bo_yl_table_5'

In [238]:
def url_to_soup(url):
    response = requests.get(url)
    page = response.text
    soup = BeautifulSoup(page,'lxml')
    return soup

In [239]:
soup = url_to_soup(url3)

In [240]:
soup

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo"><head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta charset="utf-8"/>
<title dir="ltr">Domestic Box Office For 2017 - Box Office Mojo</title><meta content="Domestic Box Office For 2017" name="title"/>
<meta content="Box Office Mojo" property="og:site_name"/>
<meta content="https://m.media-amazon.com/images/G/01/boxofficemojo/logo/mojo-logo-bg.png" property="og:image"/>
<meta content="telephone=no" name="format-detection"/>
<link href="https://m.media-amazon.com/images/G/01/boxofficemojo/v2/favicon._CB448965889_.ico" rel="icon" type="image/x-icon"/>
<link href="https://www.boxofficemojo.com/year/2017/" rel="canonical"/>
<link href="https://images-na.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41DAFIecsVL.css,51IB+wfP8qL.css,01ZfXnjPmmL.css,01oDR3IULNL.css,01Vctty9pOL.css,31ZcpBfSgNL.css,01XPHJk60-L

In [241]:
table2017 = soup.find('table')

In [242]:
rows = [row for row in table2017.find_all('tr')]

In [243]:
rows

[<tr><th class="a-text-right mojo-field-type-rank mojo-sort-column mojo-sortable-column a-nowrap"><a class="a-link-normal a-nowrap" href="?sort=rank&amp;ref_=bo_yld__resort#table" title="Rank"><span class="a-color-state">Rank</span><span class="a-letter-space"></span><span class="icon aok-relative"><i class="a-icon a-icon-collapse" role="presentation"></i></span></a></th><th class="a-text-left mojo-field-type-release mojo-cell-wide mojo-sortable-column a-nowrap"><span title="Release">Release</span>
 </th><th class="a-text-left mojo-field-type-genre hidden mojo-sortable-column hidden a-nowrap"><span title="Genre">Genre</span>
 </th><th class="a-text-right mojo-field-type-money hidden mojo-sortable-column hidden a-nowrap"><span title="Budget">Budget</span>
 </th><th class="a-text-right mojo-field-type-duration hidden mojo-sortable-column hidden a-nowrap"><span title="Running Time">Running Time</span>
 </th><th class="a-text-right mojo-field-type-money mojo-sortable-column mojo-estimatabl

In [244]:
movies2017 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2017[title] = [url, theaters, release_date, distributor]

In [245]:
movies2017

{'Star Wars: Episode VIII - The Last Jedi': ['/release/rl2708702721/?ref_=bo_yld_table_1',
  '4,232',
  'Dec 15',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Beauty and the Beast': ['/release/rl222594561/?ref_=bo_yld_table_2',
  '4,210',
  'Mar 17',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Wonder Woman': ['/release/rl578455041/?ref_=bo_yld_table_3',
  '4,165',
  'Jun 2',
  'Warner Bros.\n\n'],
 'Guardians of the Galaxy Vol. 2': ['/release/rl2976089601/?ref_=bo_yld_table_4',
  '4,347',
  'May 5',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Spider-Man: Homecoming': ['/release/rl863208961/?ref_=bo_yld_table_5',
  '4,348',
  'Jul 7',
  'Sony Pictures Entertainment (SPE)\n\n'],
 'It': ['/release/rl3481241089/?ref_=bo_yld_table_6',
  '4,148',
  'Sep 8',
  'Warner Bros.\n\n'],
 'Thor: Ragnarok': ['/release/rl2959312385/?ref_=bo_yld_table_7',
  '4,080',
  'Nov 3',
  'Walt Disney Studios Motion Pictures\n\n'],
 'Despicable Me 3': ['/release/rl122652161/?ref_=bo_yld_table_8',
  '4

In [246]:
movies2017_df = pd.DataFrame(movies2017).T

In [247]:
movies2017_df

0  \
Star Wars: Episode VIII - The Last Jedi               /release/rl2708702721/?ref_=bo_yld_table_1   
Beauty and the Beast                                   /release/rl222594561/?ref_=bo_yld_table_2   
Wonder Woman                                           /release/rl578455041/?ref_=bo_yld_table_3   
Guardians of the Galaxy Vol. 2                        /release/rl2976089601/?ref_=bo_yld_table_4   
Spider-Man: Homecoming                                 /release/rl863208961/?ref_=bo_yld_table_5   
...                                                                                          ...   
Showtime Championship Boxing: Floyd Mayweather ...   /release/rl352486913/?ref_=bo_yld_table_196   
A Question of Faith                                 /release/rl3036907009/?ref_=bo_yld_table_197   
Is Genesis History?                                 /release/rl2969601537/?ref_=bo_yld_table_198   
Disney's Newsies: The Broadway Musical!             /release/rl3204482561/?ref_=bo_yld_table_199   
IN OUR HANDS: Battle for Jerusalem                   /release/rl268666369/?ref_=bo_yld_table_200   

                                                        1       2  \
Star Wars: Episode VIII - The Last Jedi             4,232  Dec 15   
Beauty and the Beast                                4,210  Mar 17   
Wonder Woman                                        4,165   Jun 2   
Guardians of the Galaxy Vol. 2                      4,347   May 5   
Spider-Man: Homecoming                              4,348   Jul 7   
...                                                   ...     ...   
Showtime Championship Boxing: Floyd Mayweather ...    532  Aug 26   
A Question of Faith                                   661  Sep 29   
Is Genesis History?                                   704  Feb 23   
Disney's Newsies: The Broadway Musical!               780  Feb 18   
IN OUR HANDS: Battle for Jerusalem                    733  May 23   

                                                                                          3  
Star Wars: Episode VIII - The Last Jedi             Walt Disney Studios Motion Pictures\n\n  
Beauty and the Beast                                Walt Disney Studios Motion Pictures\n\n  
Wonder Woman                                                               Warner Bros.\n\n  
Guardians of the Galaxy Vol. 2                      Walt Disney Studios Motion Pictures\n\n  
Spider-Man: Homecoming                                Sony Pictures Entertainment (SPE)\n\n  
...                                                                                     ...  
Showtime Championship Boxing: Floyd Mayweather ...                        Fathom Events\n\n  
A Question of Faith                                             Pure Flix Entertainment\n\n  
Is Genesis History?                                                       Fathom Events\n\n  
Disney's Newsies: The Broadway Musical!                                   Fathom Events\n\n  
IN OUR HANDS: Battle for Jerusalem                                        Fathom Events\n\n  

[199 rows x 4 columns]

In [248]:
movies2017_df.columns = ['link', 'theaters', 'release_date', 'Distributor']

In [249]:
movies2017_df['Distributor'].replace('\n', '', regex=True, inplace=True)

In [250]:
movies2017_df['release_year'] = 2017

In [251]:
movies2017_df

link  \
Star Wars: Episode VIII - The Last Jedi               /release/rl2708702721/?ref_=bo_yld_table_1   
Beauty and the Beast                                   /release/rl222594561/?ref_=bo_yld_table_2   
Wonder Woman                                           /release/rl578455041/?ref_=bo_yld_table_3   
Guardians of the Galaxy Vol. 2                        /release/rl2976089601/?ref_=bo_yld_table_4   
Spider-Man: Homecoming                                 /release/rl863208961/?ref_=bo_yld_table_5   
...                                                                                          ...   
Showtime Championship Boxing: Floyd Mayweather ...   /release/rl352486913/?ref_=bo_yld_table_196   
A Question of Faith                                 /release/rl3036907009/?ref_=bo_yld_table_197   
Is Genesis History?                                 /release/rl2969601537/?ref_=bo_yld_table_198   
Disney's Newsies: The Broadway Musical!             /release/rl3204482561/?ref_=bo_yld_table_199   
IN OUR HANDS: Battle for Jerusalem                   /release/rl268666369/?ref_=bo_yld_table_200   

                                                   theaters release_date  \
Star Wars: Episode VIII - The Last Jedi               4,232       Dec 15   
Beauty and the Beast                                  4,210       Mar 17   
Wonder Woman                                          4,165        Jun 2   
Guardians of the Galaxy Vol. 2                        4,347        May 5   
Spider-Man: Homecoming                                4,348        Jul 7   
...                                                     ...          ...   
Showtime Championship Boxing: Floyd Mayweather ...      532       Aug 26   
A Question of Faith                                     661       Sep 29   
Is Genesis History?                                     704       Feb 23   
Disney's Newsies: The Broadway Musical!                 780       Feb 18   
IN OUR HANDS: Battle for Jerusalem                      733       May 23   

                                                                            Distributor  \
Star Wars: Episode VIII - The Last Jedi             Walt Disney Studios Motion Pictures   
Beauty and the Beast                                Walt Disney Studios Motion Pictures   
Wonder Woman                                                               Warner Bros.   
Guardians of the Galaxy Vol. 2                      Walt Disney Studios Motion Pictures   
Spider-Man: Homecoming                                Sony Pictures Entertainment (SPE)   
...                                                                                 ...   
Showtime Championship Boxing: Floyd Mayweather ...                        Fathom Events   
A Question of Faith                                             Pure Flix Entertainment   
Is Genesis History?                                                       Fathom Events   
Disney's Newsies: The Broadway Musical!                                   Fathom Events   
IN OUR HANDS: Battle for Jerusalem                                        Fathom Events   

                                                    release_year  
Star Wars: Episode VIII - The Last Jedi                     2017  
Beauty and the Beast                                        2017  
Wonder Woman                                                2017  
Guardians of the Galaxy Vol. 2                              2017  
Spider-Man: Homecoming                                      2017  
...                                                          ...  
Showtime Championship Boxing: Floyd Mayweather ...          2017  
A Question of Faith                                         2017  
Is Genesis History?                                         2017  
Disney's Newsies: The Broadway Musical!                     2017  
IN OUR HANDS: Battle for Jerusalem                          2017  

[199 rows x 5 columns]

In [252]:
movies_page_info_list_2017 = []

In [253]:
for link in movies2017_df.link:
    movies_page_info_list_2017.append(get_movie_dict(link))

In [254]:
movies_page_info_list_2017

[{'movie_title': 'Star Wars: Episode VIII',
  'genres': 'Action Adventure Fantasy Sci-Fi',
  'runtime': 152,
  'rating': 'PG-13',
  'budget': 317000000,
  'dom_gross': 620181382,
  'int_gross': 712358507},
 {'movie_title': 'Beauty and the Beast',
  'genres': 'Family Fantasy Musical Romance',
  'runtime': 129,
  'rating': 'PG',
  'budget': 160000000,
  'dom_gross': 504014165,
  'int_gross': 759506961},
 {'movie_title': 'Wonder Woman',
  'genres': 'Action Adventure Fantasy Sci-Fi War',
  'runtime': 141,
  'rating': 'PG-13',
  'budget': 149000000,
  'dom_gross': 412563408,
  'int_gross': 409283604},
 {'movie_title': 'Guardians of the Galaxy Vol. 2',
  'genres': 'Action Adventure Comedy Sci-Fi',
  'runtime': 136,
  'rating': 'PG-13',
  'budget': 200000000,
  'dom_gross': 389813101,
  'int_gross': 473942950},
 {'movie_title': 'Spider',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 133,
  'rating': 'PG-13',
  'budget': 175000000,
  'dom_gross': 334201140,
  'int_gross': 545965784},
 {'

In [255]:
movieinfo2017_df = pd.DataFrame(movies_page_info_list_2017)

In [256]:
movieinfo2017_df.set_index('movie_title', inplace=True)

In [257]:
movieinfo2017_df

genres  \
movie_title                                                                               
Star Wars: Episode VIII                                 Action Adventure Fantasy Sci-Fi   
Beauty and the Beast                                     Family Fantasy Musical Romance   
Wonder Woman                                        Action Adventure Fantasy Sci-Fi War   
Guardians of the Galaxy Vol. 2                           Action Adventure Comedy Sci-Fi   
Spider                                                          Action Adventure Sci-Fi   
...                                                                                 ...   
Showtime Championship Boxing: Floyd Mayweather ...                                Sport   
A Question of Faith                                                               Drama   
Is Genesis History?                                                         Documentary   
Disney's Newsies: The Broadway Musical!                                         Musical   
IN OUR HANDS: Battle for Jerusalem                                          Documentary   

                                                    runtime rating  \
movie_title                                                          
Star Wars: Episode VIII                               152.0  PG-13   
Beauty and the Beast                                  129.0     PG   
Wonder Woman                                          141.0  PG-13   
Guardians of the Galaxy Vol. 2                        136.0  PG-13   
Spider                                                133.0  PG-13   
...                                                     ...    ...   
Showtime Championship Boxing: Floyd Mayweather ...      NaN   None   
A Question of Faith                                   104.0     PG   
Is Genesis History?                                   100.0   None   
Disney's Newsies: The Broadway Musical!               149.0     PG   
IN OUR HANDS: Battle for Jerusalem                    109.0   None   

                                                         budget  dom_gross  \
movie_title                                                                  
Star Wars: Episode VIII                             317000000.0  620181382   
Beauty and the Beast                                160000000.0  504014165   
Wonder Woman                                        149000000.0  412563408   
Guardians of the Galaxy Vol. 2                      200000000.0  389813101   
Spider                                              175000000.0  334201140   
...                                                         ...        ...   
Showtime Championship Boxing: Floyd Mayweather ...          NaN    2620183   
A Question of Faith                                         NaN    2587072   
Is Genesis History?                                         NaN    2570392   
Disney's Newsies: The Broadway Musical!                     NaN    2545060   
IN OUR HANDS: Battle for Jerusalem                          NaN    2534370   

                                                    int_gross  
movie_title                                                    
Star Wars: Episode VIII                             712358507  
Beauty and the Beast                                759506961  
Wonder Woman                                        409283604  
Guardians of the Galaxy Vol. 2                      473942950  
Spider                                              545965784  
...                                                       ...  
Showtime Championship Boxing: Floyd Mayweather ...     564201  
A Question of Faith                                   2587072  
Is Genesis History?                                   2570392  
Disney's Newsies: The Broadway Musical!               2545060  
IN OUR HANDS: Battle for Jerusalem                    2534370  

[199 rows x 6 columns]

In [258]:
movieinfo2017_df.isna().sum()

genres        0
runtime       6
rating       12
budget       78
dom_gross     0
int_gross     0
dtype: int64

In [259]:
movies2017_df = movies2017_df.merge(movieinfo2017_df, left_index=True, right_index=True)

In [260]:
movies2017_df

link  \
Beauty and the Beast                                   /release/rl222594561/?ref_=bo_yld_table_2   
Wonder Woman                                           /release/rl578455041/?ref_=bo_yld_table_3   
Guardians of the Galaxy Vol. 2                        /release/rl2976089601/?ref_=bo_yld_table_4   
It                                                    /release/rl3481241089/?ref_=bo_yld_table_6   
Thor: Ragnarok                                        /release/rl2959312385/?ref_=bo_yld_table_7   
...                                                                                          ...   
Showtime Championship Boxing: Floyd Mayweather ...   /release/rl352486913/?ref_=bo_yld_table_196   
A Question of Faith                                 /release/rl3036907009/?ref_=bo_yld_table_197   
Is Genesis History?                                 /release/rl2969601537/?ref_=bo_yld_table_198   
Disney's Newsies: The Broadway Musical!             /release/rl3204482561/?ref_=bo_yld_table_199   
IN OUR HANDS: Battle for Jerusalem                   /release/rl268666369/?ref_=bo_yld_table_200   

                                                   theaters release_date  \
Beauty and the Beast                                  4,210       Mar 17   
Wonder Woman                                          4,165        Jun 2   
Guardians of the Galaxy Vol. 2                        4,347        May 5   
It                                                    4,148        Sep 8   
Thor: Ragnarok                                        4,080        Nov 3   
...                                                     ...          ...   
Showtime Championship Boxing: Floyd Mayweather ...      532       Aug 26   
A Question of Faith                                     661       Sep 29   
Is Genesis History?                                     704       Feb 23   
Disney's Newsies: The Broadway Musical!                 780       Feb 18   
IN OUR HANDS: Battle for Jerusalem                      733       May 23   

                                                                            Distributor  \
Beauty and the Beast                                Walt Disney Studios Motion Pictures   
Wonder Woman                                                               Warner Bros.   
Guardians of the Galaxy Vol. 2                      Walt Disney Studios Motion Pictures   
It                                                                         Warner Bros.   
Thor: Ragnarok                                      Walt Disney Studios Motion Pictures   
...                                                                                 ...   
Showtime Championship Boxing: Floyd Mayweather ...                        Fathom Events   
A Question of Faith                                             Pure Flix Entertainment   
Is Genesis History?                                                       Fathom Events   
Disney's Newsies: The Broadway Musical!                                   Fathom Events   
IN OUR HANDS: Battle for Jerusalem                                        Fathom Events   

                                                    release_year  \
Beauty and the Beast                                        2017   
Wonder Woman                                                2017   
Guardians of the Galaxy Vol. 2                              2017   
It                                                          2017   
Thor: Ragnarok                                              2017   
...                                                          ...   
Showtime Championship Boxing: Floyd Mayweather ...          2017   
A Question of Faith                                         2017   
Is Genesis History?                                         2017   
Disney's Newsies: The Broadway Musical!                     2017   
IN OUR HANDS: Battle for Jerusalem                          2017   

                                                                    

In [261]:
movies2017_df.to_csv('movies_2017')

In [262]:
#requesting movies for 2016
url4 = 'https://www.boxofficemojo.com/year/2016/?ref_=bo_yl_table_6'

In [263]:
soup = url_to_soup(url4)

In [264]:
soup

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo"><head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta charset="utf-8"/>
<title dir="ltr">Domestic Box Office For 2016 - Box Office Mojo</title><meta content="Domestic Box Office For 2016" name="title"/>
<meta content="Box Office Mojo" property="og:site_name"/>
<meta content="https://m.media-amazon.com/images/G/01/boxofficemojo/logo/mojo-logo-bg.png" property="og:image"/>
<meta content="telephone=no" name="format-detection"/>
<link href="https://m.media-amazon.com/images/G/01/boxofficemojo/v2/favicon._CB448965889_.ico" rel="icon" type="image/x-icon"/>
<link href="https://www.boxofficemojo.com/year/2016/" rel="canonical"/>
<link href="https://images-na.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41DAFIecsVL.css,51IB+wfP8qL.css,01ZfXnjPmmL.css,01oDR3IULNL.css,01Vctty9pOL.css,31ZcpBfSgNL.css,01XPHJk60-L

In [265]:
table2016 = soup.find('table')

In [266]:
rows = [row for row in table2016.find_all('tr')]

In [267]:
rows

[<tr><th class="a-text-right mojo-field-type-rank mojo-sort-column mojo-sortable-column a-nowrap"><a class="a-link-normal a-nowrap" href="?sort=rank&amp;ref_=bo_yld__resort#table" title="Rank"><span class="a-color-state">Rank</span><span class="a-letter-space"></span><span class="icon aok-relative"><i class="a-icon a-icon-collapse" role="presentation"></i></span></a></th><th class="a-text-left mojo-field-type-release mojo-cell-wide mojo-sortable-column a-nowrap"><span title="Release">Release</span>
 </th><th class="a-text-left mojo-field-type-genre hidden mojo-sortable-column hidden a-nowrap"><span title="Genre">Genre</span>
 </th><th class="a-text-right mojo-field-type-money hidden mojo-sortable-column hidden a-nowrap"><span title="Budget">Budget</span>
 </th><th class="a-text-right mojo-field-type-duration hidden mojo-sortable-column hidden a-nowrap"><span title="Running Time">Running Time</span>
 </th><th class="a-text-right mojo-field-type-money mojo-sortable-column mojo-estimatabl

In [268]:
movies2016 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2016[title] = [url, theaters, release_date, distributor]

In [269]:
movies2016_df = pd.DataFrame(movies2016).T

In [270]:
movies2016_df

0  \
Finding Dory                    /release/rl3764946433/?ref_=bo_yld_table_1   
Rogue One: A Star Wars Story    /release/rl2557707777/?ref_=bo_yld_table_2   
Captain America: Civil War      /release/rl3210970625/?ref_=bo_yld_table_3   
The Secret Life of Pets         /release/rl2069595649/?ref_=bo_yld_table_4   
The Jungle Book                 /release/rl2455602689/?ref_=bo_yld_table_5   
...                                                                    ...   
Green Room                     /release/rl360482305/?ref_=bo_yld_table_196   
Our Kind of Traitor           /release/rl4101998081/?ref_=bo_yld_table_197   
Compadres                     /release/rl3950806529/?ref_=bo_yld_table_198   
The Martian                   /release/rl3496969729/?ref_=bo_yld_table_199   
The Other Side of the Door    /release/rl3715991041/?ref_=bo_yld_table_200   

                                  1       2  \
Finding Dory                  4,305  Jun 17   
Rogue One: A Star Wars Story  4,157  Dec 16   
Captain America: Civil War    4,226   May 6   
The Secret Life of Pets       4,381   Jul 8   
The Jungle Book               4,144  Apr 15   
...                             ...     ...   
Green Room                      777  Apr 15   
Our Kind of Traitor             399   Jul 1   
Compadres                       368  Apr 22   
The Martian                   3,854   Oct 2   
The Other Side of the Door      585   Mar 4   

                                                                    3  
Finding Dory                  Walt Disney Studios Motion Pictures\n\n  
Rogue One: A Star Wars Story  Walt Disney Studios Motion Pictures\n\n  
Captain America: Civil War    Walt Disney Studios Motion Pictures\n\n  
The Secret Life of Pets                        Universal Pictures\n\n  
The Jungle Book               Walt Disney Studios Motion Pictures\n\n  
...                                                               ...  
Green Room                                                    A24\n\n  
Our Kind of Traitor                          Roadside Attractions\n\n  
Compadres                                         Pantelion Films\n\n  
The Martian                                 Twentieth Century Fox\n\n  
The Other Side of the Door                  Twentieth Century Fox\n\n  

[200 rows x 4 columns]

In [271]:
movies2016_df.columns = ['link', 'theaters', 'release_date', 'Distributor']
movies2016_df['Distributor'].replace('\n', '', regex=True, inplace=True)
movies2016_df['release_year'] = 2016

In [272]:
movies2016_df

link  \
Finding Dory                    /release/rl3764946433/?ref_=bo_yld_table_1   
Rogue One: A Star Wars Story    /release/rl2557707777/?ref_=bo_yld_table_2   
Captain America: Civil War      /release/rl3210970625/?ref_=bo_yld_table_3   
The Secret Life of Pets         /release/rl2069595649/?ref_=bo_yld_table_4   
The Jungle Book                 /release/rl2455602689/?ref_=bo_yld_table_5   
...                                                                    ...   
Green Room                     /release/rl360482305/?ref_=bo_yld_table_196   
Our Kind of Traitor           /release/rl4101998081/?ref_=bo_yld_table_197   
Compadres                     /release/rl3950806529/?ref_=bo_yld_table_198   
The Martian                   /release/rl3496969729/?ref_=bo_yld_table_199   
The Other Side of the Door    /release/rl3715991041/?ref_=bo_yld_table_200   

                             theaters release_date  \
Finding Dory                    4,305       Jun 17   
Rogue One: A Star Wars Story    4,157       Dec 16   
Captain America: Civil War      4,226        May 6   
The Secret Life of Pets         4,381        Jul 8   
The Jungle Book                 4,144       Apr 15   
...                               ...          ...   
Green Room                        777       Apr 15   
Our Kind of Traitor               399        Jul 1   
Compadres                         368       Apr 22   
The Martian                     3,854        Oct 2   
The Other Side of the Door        585        Mar 4   

                                                      Distributor  \
Finding Dory                  Walt Disney Studios Motion Pictures   
Rogue One: A Star Wars Story  Walt Disney Studios Motion Pictures   
Captain America: Civil War    Walt Disney Studios Motion Pictures   
The Secret Life of Pets                        Universal Pictures   
The Jungle Book               Walt Disney Studios Motion Pictures   
...                                                           ...   
Green Room                                                    A24   
Our Kind of Traitor                          Roadside Attractions   
Compadres                                         Pantelion Films   
The Martian                                 Twentieth Century Fox   
The Other Side of the Door                  Twentieth Century Fox   

                              release_year  
Finding Dory                          2016  
Rogue One: A Star Wars Story          2016  
Captain America: Civil War            2016  
The Secret Life of Pets               2016  
The Jungle Book                       2016  
...                                    ...  
Green Room                            2016  
Our Kind of Traitor                   2016  
Compadres                             2016  
The Martian                           2016  
The Other Side of the Door            2016  

[200 rows x 5 columns]

In [273]:
movies_page_info_list_2016 = []

In [274]:
for link in movies2016_df.link:
    movies_page_info_list_2016.append(get_movie_dict(link))

In [275]:
movies_page_info_list_2016

[{'movie_title': 'Finding Dory',
  'genres': 'Adventure Animation Comedy Family',
  'runtime': 97,
  'rating': 'PG',
  'budget': None,
  'dom_gross': 486295561,
  'int_gross': 542275328},
 {'movie_title': 'Rogue One: A Star Wars Story',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 133,
  'rating': 'PG-13',
  'budget': 200000000,
  'dom_gross': 532177324,
  'int_gross': 523879949},
 {'movie_title': 'Captain America: Civil War',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 147,
  'rating': 'PG-13',
  'budget': 250000000,
  'dom_gross': 408084349,
  'int_gross': 745211944},
 {'movie_title': 'The Secret Life of Pets',
  'genres': 'Adventure Animation Comedy Family',
  'runtime': 87,
  'rating': 'PG',
  'budget': 75000000,
  'dom_gross': 368384330,
  'int_gross': 507073607},
 {'movie_title': 'The Jungle Book',
  'genres': 'Adventure Animation Comedy Drama Family Fantasy Musical',
  'runtime': 106,
  'rating': 'PG',
  'budget': 175000000,
  'dom_gross': 364001123,
  'int_gross'

In [276]:
movieinfo2016_df = pd.DataFrame(movies_page_info_list_2016)

In [277]:
movieinfo2016_df.set_index('movie_title', inplace=True)

In [278]:
movieinfo2016_df.isna().sum()

genres        0
runtime       6
rating        5
budget       82
dom_gross     0
int_gross     0
dtype: int64

In [279]:
movies2016_df = movies2016_df.merge(movieinfo2016_df, left_index=True, right_index=True)

In [280]:
movies2016_df

link  \
Finding Dory                    /release/rl3764946433/?ref_=bo_yld_table_1   
Rogue One: A Star Wars Story    /release/rl2557707777/?ref_=bo_yld_table_2   
Captain America: Civil War      /release/rl3210970625/?ref_=bo_yld_table_3   
The Secret Life of Pets         /release/rl2069595649/?ref_=bo_yld_table_4   
The Jungle Book                 /release/rl2455602689/?ref_=bo_yld_table_5   
...                                                                    ...   
Green Room                     /release/rl360482305/?ref_=bo_yld_table_196   
Our Kind of Traitor           /release/rl4101998081/?ref_=bo_yld_table_197   
Compadres                     /release/rl3950806529/?ref_=bo_yld_table_198   
The Martian                   /release/rl3496969729/?ref_=bo_yld_table_199   
The Other Side of the Door    /release/rl3715991041/?ref_=bo_yld_table_200   

                             theaters release_date  \
Finding Dory                    4,305       Jun 17   
Rogue One: A Star Wars Story    4,157       Dec 16   
Captain America: Civil War      4,226        May 6   
The Secret Life of Pets         4,381        Jul 8   
The Jungle Book                 4,144       Apr 15   
...                               ...          ...   
Green Room                        777       Apr 15   
Our Kind of Traitor               399        Jul 1   
Compadres                         368       Apr 22   
The Martian                     3,854        Oct 2   
The Other Side of the Door        585        Mar 4   

                                                      Distributor  \
Finding Dory                  Walt Disney Studios Motion Pictures   
Rogue One: A Star Wars Story  Walt Disney Studios Motion Pictures   
Captain America: Civil War    Walt Disney Studios Motion Pictures   
The Secret Life of Pets                        Universal Pictures   
The Jungle Book               Walt Disney Studios Motion Pictures   
...                                                           ...   
Green Room                                                    A24   
Our Kind of Traitor                          Roadside Attractions   
Compadres                                         Pantelion Films   
The Martian                                 Twentieth Century Fox   
The Other Side of the Door                  Twentieth Century Fox   

                              release_year  \
Finding Dory                          2016   
Rogue One: A Star Wars Story          2016   
Captain America: Civil War            2016   
The Secret Life of Pets               2016   
The Jungle Book                       2016   
...                                    ...   
Green Room                            2016   
Our Kind of Traitor                   2016   
Compadres                             2016   
The Martian                           2016   
The Other Side of the Door            2016   

                                                                         genres  \
Finding Dory                                  Adventure Animation Comedy Family   
Rogue One: A Star Wars Story                            Action Adventure Sci-Fi   
Captain America: Civil War                              Action Adventure Sci-Fi   
The Secret Life of Pets                       Adventure Animation Comedy Family   
The Jungle Book               Adventure Animation Comedy Drama Family Fantas...   
...                                                                         ...   
Green Room                                                      Horror Thriller   
Our Kind of Traitor                                        Crime Drama Thriller   
Compadres                                                   Action Comedy Crime   
The Martian                                              Adventure Drama Sci-Fi   
The Other Side of the Door                                               Horror   

                              runtime rating       budget  dom_gross  \
Finding Dory                     

In [281]:
movies2016_df.to_csv('movies_2016')

In [282]:
#requesting movies for 2015
url5 = 'https://www.boxofficemojo.com/year/2015/?ref_=bo_yl_table_7'

In [283]:
soup = url_to_soup(url5)

In [284]:
soup

<!DOCTYPE html>
<html class="a-no-js" data-19ax5a9jf="dingo"><head><script>var aPageStart = (new Date()).getTime();</script><meta charset="utf-8"/><meta content="width=device-width, initial-scale=1.0" name="viewport"/>
<meta charset="utf-8"/>
<title dir="ltr">Domestic Box Office For 2015 - Box Office Mojo</title><meta content="Domestic Box Office For 2015" name="title"/>
<meta content="Box Office Mojo" property="og:site_name"/>
<meta content="https://m.media-amazon.com/images/G/01/boxofficemojo/logo/mojo-logo-bg.png" property="og:image"/>
<meta content="telephone=no" name="format-detection"/>
<link href="https://m.media-amazon.com/images/G/01/boxofficemojo/v2/favicon._CB448965889_.ico" rel="icon" type="image/x-icon"/>
<link href="https://www.boxofficemojo.com/year/2015/" rel="canonical"/>
<link href="https://images-na.ssl-images-amazon.com/images/I/11EIQ5IGqaL._RC|01ZTHTZObnL.css,41DAFIecsVL.css,51IB+wfP8qL.css,01ZfXnjPmmL.css,01oDR3IULNL.css,01Vctty9pOL.css,31ZcpBfSgNL.css,01XPHJk60-L

In [285]:
table2015 = soup.find('table')

In [286]:
rows = [row for row in table2015.find_all('tr')]

In [287]:
rows

[<tr><th class="a-text-right mojo-field-type-rank mojo-sort-column mojo-sortable-column a-nowrap"><a class="a-link-normal a-nowrap" href="?sort=rank&amp;ref_=bo_yld__resort#table" title="Rank"><span class="a-color-state">Rank</span><span class="a-letter-space"></span><span class="icon aok-relative"><i class="a-icon a-icon-collapse" role="presentation"></i></span></a></th><th class="a-text-left mojo-field-type-release mojo-cell-wide mojo-sortable-column a-nowrap"><span title="Release">Release</span>
 </th><th class="a-text-left mojo-field-type-genre hidden mojo-sortable-column hidden a-nowrap"><span title="Genre">Genre</span>
 </th><th class="a-text-right mojo-field-type-money hidden mojo-sortable-column hidden a-nowrap"><span title="Budget">Budget</span>
 </th><th class="a-text-right mojo-field-type-duration hidden mojo-sortable-column hidden a-nowrap"><span title="Running Time">Running Time</span>
 </th><th class="a-text-right mojo-field-type-money mojo-sortable-column mojo-estimatabl

In [288]:
movies2015 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2015[title] = [url, theaters, release_date, distributor]

In [289]:
movies2015_df = pd.DataFrame(movies2015).T

In [290]:
movies2015_df

0  \
Jurassic World                                       /release/rl2371716609/?ref_=bo_yld_table_1   
Star Wars: Episode VII - The Force Awakens           /release/rl2691925505/?ref_=bo_yld_table_2   
Avengers: Age of Ultron                               /release/rl675644929/?ref_=bo_yld_table_3   
Inside Out                                           /release/rl4016604673/?ref_=bo_yld_table_4   
Furious 7                                            /release/rl1045661185/?ref_=bo_yld_table_5   
...                                                                                         ...   
Truth                                              /release/rl1316849153/?ref_=bo_yld_table_196   
Mistress America                                   /release/rl3462563329/?ref_=bo_yld_table_197   
Pawn Sacrifice                                     /release/rl1063814657/?ref_=bo_yld_table_198   
The Oscar Nominated Short Films 2015: Live Action  /release/rl1648461313/?ref_=bo_yld_table_199   
Meru                                               /release/rl2793244161/?ref_=bo_yld_table_200   

                                                       1       2  \
Jurassic World                                     4,291  Jun 12   
Star Wars: Episode VII - The Force Awakens         4,134  Dec 18   
Avengers: Age of Ultron                            4,276   May 1   
Inside Out                                         4,158  Jun 19   
Furious 7                                          4,022   Apr 3   
...                                                  ...     ...   
Truth                                              1,122  Oct 16   
Mistress America                                     512  Aug 14   
Pawn Sacrifice                                       781  Sep 16   
The Oscar Nominated Short Films 2015: Live Action    280  Jan 30   
Meru                                                 176  Aug 14   

                                                                                         3  
Jurassic World                                                      Universal Pictures\n\n  
Star Wars: Episode VII - The Force Awakens         Walt Disney Studios Motion Pictures\n\n  
Avengers: Age of Ultron                            Walt Disney Studios Motion Pictures\n\n  
Inside Out                                         Walt Disney Studios Motion Pictures\n\n  
Furious 7                                                           Universal Pictures\n\n  
...                                                                                    ...  
Truth                                                           Sony Pictures Classics\n\n  
Mistress America                                              Fox Searchlight Pictures\n\n  
Pawn Sacrifice                                                   Bleecker Street Media\n\n  
The Oscar Nominated Short Films 2015: Live Action                 Shorts International\n\n  
Meru                                                                   Music Box Films\n\n  

[200 rows x 4 columns]

In [291]:
movies2015_df.columns = ['link', 'theaters', 'release_date', 'Distributor']
movies2015_df['Distributor'].replace('\n', '', regex=True, inplace=True)
movies2015_df['release_year'] = 2015

In [292]:
movies2015_df

link  \
Jurassic World                                       /release/rl2371716609/?ref_=bo_yld_table_1   
Star Wars: Episode VII - The Force Awakens           /release/rl2691925505/?ref_=bo_yld_table_2   
Avengers: Age of Ultron                               /release/rl675644929/?ref_=bo_yld_table_3   
Inside Out                                           /release/rl4016604673/?ref_=bo_yld_table_4   
Furious 7                                            /release/rl1045661185/?ref_=bo_yld_table_5   
...                                                                                         ...   
Truth                                              /release/rl1316849153/?ref_=bo_yld_table_196   
Mistress America                                   /release/rl3462563329/?ref_=bo_yld_table_197   
Pawn Sacrifice                                     /release/rl1063814657/?ref_=bo_yld_table_198   
The Oscar Nominated Short Films 2015: Live Action  /release/rl1648461313/?ref_=bo_yld_table_199   
Meru                                               /release/rl2793244161/?ref_=bo_yld_table_200   

                                                  theaters release_date  \
Jurassic World                                       4,291       Jun 12   
Star Wars: Episode VII - The Force Awakens           4,134       Dec 18   
Avengers: Age of Ultron                              4,276        May 1   
Inside Out                                           4,158       Jun 19   
Furious 7                                            4,022        Apr 3   
...                                                    ...          ...   
Truth                                                1,122       Oct 16   
Mistress America                                       512       Aug 14   
Pawn Sacrifice                                         781       Sep 16   
The Oscar Nominated Short Films 2015: Live Action      280       Jan 30   
Meru                                                   176       Aug 14   

                                                                           Distributor  \
Jurassic World                                                      Universal Pictures   
Star Wars: Episode VII - The Force Awakens         Walt Disney Studios Motion Pictures   
Avengers: Age of Ultron                            Walt Disney Studios Motion Pictures   
Inside Out                                         Walt Disney Studios Motion Pictures   
Furious 7                                                           Universal Pictures   
...                                                                                ...   
Truth                                                           Sony Pictures Classics   
Mistress America                                              Fox Searchlight Pictures   
Pawn Sacrifice                                                   Bleecker Street Media   
The Oscar Nominated Short Films 2015: Live Action                 Shorts International   
Meru                                                                   Music Box Films   

                                                   release_year  
Jurassic World                                             2015  
Star Wars: Episode VII - The Force Awakens                 2015  
Avengers: Age of Ultron                                    2015  
Inside Out                                                 2015  
Furious 7                                                  2015  
...                                                         ...  
Truth                                                      2015  
Mistress America                                           2015  
Pawn Sacrifice                                             2015  
The Oscar Nominated Short Films 2015: Live Action          2015  
Meru                                                       2015  

[200 rows x 5 columns]

In [293]:
movies_page_info_list_2015 = []

In [294]:
for link in movies2015_df.link:
    movies_page_info_list_2015.append(get_movie_dict(link))

In [295]:
movies_page_info_list_2015

[{'movie_title': 'Jurassic World',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 124,
  'rating': 'PG-13',
  'budget': 150000000,
  'dom_gross': 652270625,
  'int_gross': 1018130012},
 {'movie_title': 'Star Wars: Episode VII',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 138,
  'rating': 'PG-13',
  'budget': 245000000,
  'dom_gross': 936662225,
  'int_gross': 1131561399},
 {'movie_title': 'Avengers: Age of Ultron',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 141,
  'rating': 'PG-13',
  'budget': 250000000,
  'dom_gross': 459005868,
  'int_gross': 943800000},
 {'movie_title': 'Inside Out',
  'genres': 'Adventure Animation Comedy Family Fantasy',
  'runtime': 95,
  'rating': 'PG',
  'budget': 175000000,
  'dom_gross': 356461711,
  'int_gross': 501149463},
 {'movie_title': 'Furious 7',
  'genres': 'Action Adventure Thriller',
  'runtime': 137,
  'rating': 'PG-13',
  'budget': 190000000,
  'dom_gross': 353007020,
  'int_gross': 1162040651},
 {'movie_title': 'American S

In [296]:
movieinfo2015_df = pd.DataFrame(movies_page_info_list_2015)

In [297]:
movieinfo2015_df.set_index('movie_title', inplace=True)

In [298]:
movieinfo2015_df.isna().sum()

genres        0
runtime       6
rating       11
budget       70
dom_gross     0
int_gross     0
dtype: int64

In [299]:
movies2015_df = movies2015_df.merge(movieinfo2015_df, left_index=True, right_index=True)

In [300]:
movies2015_df

link theaters  \
90 Minutes in Heaven  /release/rl2759689729/?ref_=bo_yld_table_165      899   
A Most Violent Year   /release/rl3110438401/?ref_=bo_yld_table_160      818   
A Walk in the Woods    /release/rl3547956737/?ref_=bo_yld_table_84    2,158   
A la mala             /release/rl3896542721/?ref_=bo_yld_table_178      384   
Aloha                 /release/rl2790098433/?ref_=bo_yld_table_104    2,815   
...                                                            ...      ...   
Whiplash               /release/rl914064897/?ref_=bo_yld_table_149      567   
Wild                  /release/rl1367049729/?ref_=bo_yld_table_110    1,361   
Wild Tales            /release/rl3195766273/?ref_=bo_yld_table_190      122   
Woman in Gold           /release/rl981108225/?ref_=bo_yld_table_77    2,011   
Woodlawn              /release/rl2742912513/?ref_=bo_yld_table_124    1,553   

                     release_date                        Distributor  \
90 Minutes in Heaven       Sep 11         The Samuel Goldwyn Company   
A Most Violent Year        Dec 31                                A24   
A Walk in the Woods         Sep 2               Broad Green Pictures   
A la mala                  Feb 27                          Lionsgate   
Aloha                      May 29  Sony Pictures Entertainment (SPE)   
...                           ...                                ...   
Whiplash                   Oct 10             Sony Pictures Classics   
Wild                        Dec 3           Fox Searchlight Pictures   
Wild Tales                 Feb 20             Sony Pictures Classics   
Woman in Gold               Apr 1              The Weinstein Company   
Woodlawn                   Oct 16            Pure Flix Entertainment   

                      release_year                            genres  runtime  \
90 Minutes in Heaven          2015                             Drama    121.0   
A Most Violent Year           2015       Action Crime Drama Thriller    125.0   
A Walk in the Woods           2015  Adventure Biography Comedy Drama    104.0   
A la mala                     2015                            Comedy     99.0   
Aloha                         2015              Comedy Drama Romance    105.0   
...                            ...                               ...      ...   
Whiplash                      2015                       Drama Music    106.0   
Wild                          2015         Adventure Biography Drama    115.0   
Wild Tales                    2015             Comedy Drama Thriller    122.0   
Woman in Gold                 2015           Biography Drama History    109.0   
Woodlawn                      2015     Biography Drama History Sport    123.0   

                     rating      budget  dom_gross  int_gross  
90 Minutes in Heaven  PG-13   5000000.0    4842699    4842699  
A Most Violent Year       R  20000000.0    5749134    6257936  
A Walk in the Woods       R         NaN   29504281    7956993  
A la mala             PG-13         NaN    3629842      16785  
Aloha                 PG-13  37000000.0   21067116    5182904  
...                     ...         ...        ...        ...  
Whiplash                  R   3300000.0   13092000   35890041  
Wild                      R         NaN   37880356   14621185  
Wild Tales                R         NaN    3106530   27536174  
Woman in Gold         PG-13  11000000.0   33307793   28311980  
Woodlawn                 PG         NaN   14394097       7520  

[193 rows x 11 columns]

In [301]:
movies2015_df.to_csv('movies_2015')

In [302]:
#requesting movies for 2014
url6 = 'https://www.boxofficemojo.com/year/2014/?ref_=bo_yl_table_8'

In [303]:
soup = url_to_soup(url6)

In [304]:
table2014 = soup.find('table')
rows = [row for row in table2014.find_all('tr')]

In [305]:
movies2014 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2014[title] = [url, theaters, release_date, distributor]

In [306]:
movies2014_df = pd.DataFrame(movies2014).T

In [307]:
movies2014_df.columns = ['link', 'theaters', 'release_date', 'Distributor']
movies2014_df['Distributor'].replace('\n', '', regex=True, inplace=True)
movies2014_df['release_year'] = 2014

In [308]:
movies2014_df

link  \
Guardians of the Galaxy                  /release/rl3177416193/?ref_=bo_yld_table_1   
The Hunger Games: Mockingjay - Part 1    /release/rl4283991553/?ref_=bo_yld_table_2   
Captain America: The Winter Soldier      /release/rl3194193409/?ref_=bo_yld_table_3   
The Lego Movie                            /release/rl643728897/?ref_=bo_yld_table_4   
Transformers: Age of Extinction          /release/rl2960623105/?ref_=bo_yld_table_5   
...                                                                             ...   
Under the Skin                         /release/rl4202071553/?ref_=bo_yld_table_196   
The Admiral: Roaring Currents          /release/rl1614841345/?ref_=bo_yld_table_197   
Dragon Ball Z: Battle of Gods          /release/rl1431209473/?ref_=bo_yld_table_198   
Bang Bang                              /release/rl2521138689/?ref_=bo_yld_table_199   
Kick                                    /release/rl274499073/?ref_=bo_yld_table_200   

                                      theaters release_date  \
Guardians of the Galaxy                  4,088        Aug 1   
The Hunger Games: Mockingjay - Part 1    4,151       Nov 21   
Captain America: The Winter Soldier      3,938        Apr 4   
The Lego Movie                           3,890        Feb 7   
Transformers: Age of Extinction          4,233       Jun 27   
...                                        ...          ...   
Under the Skin                             176        Apr 4   
The Admiral: Roaring Currents               45        Aug 8   
Dragon Ball Z: Battle of Gods              692        Aug 5   
Bang Bang                                  271        Oct 2   
Kick                                       180       Jul 25   

                                                               Distributor  \
Guardians of the Galaxy                Walt Disney Studios Motion Pictures   
The Hunger Games: Mockingjay - Part 1                            Lionsgate   
Captain America: The Winter Soldier    Walt Disney Studios Motion Pictures   
The Lego Movie                                                Warner Bros.   
Transformers: Age of Extinction                         Paramount Pictures   
...                                                                    ...   
Under the Skin                                                         A24   
The Admiral: Roaring Currents                             CJ Entertainment   
Dragon Ball Z: Battle of Gods                                 Screenvision   
Bang Bang                                                              FIP   
Kick                                                   UTV Motion Pictures   

                                       release_year  
Guardians of the Galaxy                        2014  
The Hunger Games: Mockingjay - Part 1          2014  
Captain America: The Winter Soldier            2014  
The Lego Movie                                 2014  
Transformers: Age of Extinction                2014  
...                                             ...  
Under the Skin                                 2014  
The Admiral: Roaring Currents                  2014  
Dragon Ball Z: Battle of Gods                  2014  
Bang Bang                                      2014  
Kick                                           2014  

[200 rows x 5 columns]

In [310]:
movies_page_info_list_2014 = []
for link in movies2014_df.link:
    movies_page_info_list_2014.append(get_movie_dict(link))

In [311]:
movies_page_info_list_2014

[{'movie_title': 'Guardians of the Galaxy',
  'genres': 'Action Adventure Comedy Sci-Fi',
  'runtime': 121,
  'rating': 'PG-13',
  'budget': 170000000,
  'dom_gross': 333176600,
  'int_gross': 439600000},
 {'movie_title': 'The Hunger Games: Mockingjay',
  'genres': 'Action Adventure Sci-Fi Thriller',
  'runtime': 123,
  'rating': 'PG-13',
  'budget': 125000000,
  'dom_gross': 337135885,
  'int_gross': 418220826},
 {'movie_title': 'Captain America: The Winter Soldier',
  'genres': 'Action Adventure Sci-Fi Thriller',
  'runtime': 136,
  'rating': 'PG-13',
  'budget': 170000000,
  'dom_gross': 259766572,
  'int_gross': 454654931},
 {'movie_title': 'The Lego Movie',
  'genres': 'Adventure Animation Comedy Family Fantasy Sci-Fi',
  'runtime': 100,
  'rating': 'PG',
  'budget': 60000000,
  'dom_gross': 257760692,
  'int_gross': 210300000},
 {'movie_title': 'Transformers: Age of Extinction',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 165,
  'rating': 'PG-13',
  'budget': 210000000,
 

In [312]:
movieinfo2014_df = pd.DataFrame(movies_page_info_list_2014)
movieinfo2014_df.set_index('movie_title', inplace=True)

In [313]:
movieinfo2014_df.isna().sum()

genres        0
runtime       6
rating       12
budget       74
dom_gross     0
int_gross     0
dtype: int64

In [314]:
movies2014_df = movies2014_df.merge(movieinfo2014_df, left_index=True, right_index=True)

In [315]:
movies2014_df

link  \
Guardians of the Galaxy                /release/rl3177416193/?ref_=bo_yld_table_1   
Captain America: The Winter Soldier    /release/rl3194193409/?ref_=bo_yld_table_3   
The Lego Movie                          /release/rl643728897/?ref_=bo_yld_table_4   
Transformers: Age of Extinction        /release/rl2960623105/?ref_=bo_yld_table_5   
Maleficent                             /release/rl3915417089/?ref_=bo_yld_table_6   
...                                                                           ...   
Under the Skin                       /release/rl4202071553/?ref_=bo_yld_table_196   
The Admiral: Roaring Currents        /release/rl1614841345/?ref_=bo_yld_table_197   
Dragon Ball Z: Battle of Gods        /release/rl1431209473/?ref_=bo_yld_table_198   
Bang Bang                            /release/rl2521138689/?ref_=bo_yld_table_199   
Kick                                  /release/rl274499073/?ref_=bo_yld_table_200   

                                    theaters release_date  \
Guardians of the Galaxy                4,088        Aug 1   
Captain America: The Winter Soldier    3,938        Apr 4   
The Lego Movie                         3,890        Feb 7   
Transformers: Age of Extinction        4,233       Jun 27   
Maleficent                             3,948       May 30   
...                                      ...          ...   
Under the Skin                           176        Apr 4   
The Admiral: Roaring Currents             45        Aug 8   
Dragon Ball Z: Battle of Gods            692        Aug 5   
Bang Bang                                271        Oct 2   
Kick                                     180       Jul 25   

                                                             Distributor  \
Guardians of the Galaxy              Walt Disney Studios Motion Pictures   
Captain America: The Winter Soldier  Walt Disney Studios Motion Pictures   
The Lego Movie                                              Warner Bros.   
Transformers: Age of Extinction                       Paramount Pictures   
Maleficent                           Walt Disney Studios Motion Pictures   
...                                                                  ...   
Under the Skin                                                       A24   
The Admiral: Roaring Currents                           CJ Entertainment   
Dragon Ball Z: Battle of Gods                               Screenvision   
Bang Bang                                                            FIP   
Kick                                                 UTV Motion Pictures   

                                     release_year  \
Guardians of the Galaxy                      2014   
Captain America: The Winter Soldier          2014   
The Lego Movie                               2014   
Transformers: Age of Extinction              2014   
Maleficent                                   2014   
...                                           ...   
Under the Skin                               2014   
The Admiral: Roaring Currents                2014   
Dragon Ball Z: Battle of Gods                2014   
Bang Bang                                    2014   
Kick                                         2014   

                                                                                genres  \
Guardians of the Galaxy                                 Action Adventure Comedy Sci-Fi   
Captain America: The Winter Soldier                   Action Adventure Sci-Fi Thriller   
The Lego Movie                        Adventure Animation Comedy Family Fantasy Sci-Fi   
Transformers: Age of Extinction                                Action Adventure Sci-Fi   
Maleficent                                     Action Adventure Family Fantasy Romance   
...                                                                                ...   
Under the Skin                                            Drama Horror Sci-Fi Thriller   
The Admiral: Roaring Currents                        

In [316]:
movies2014_df.to_csv('movies_2014')

In [317]:
#requesting movies for 2013
url7 = 'https://www.boxofficemojo.com/year/2013/?ref_=bo_yl_table_9'
soup = url_to_soup(url7)

In [318]:
table2013 = soup.find('table')
rows = [row for row in table2013.find_all('tr')]

In [319]:
movies2013 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2013[title] = [url, theaters, release_date, distributor]

In [320]:
movies2013_df = pd.DataFrame(movies2013).T
movies2013_df.columns = ['link', 'theaters', 'release_date', 'Distributor']
movies2013_df['Distributor'].replace('\n', '', regex=True, inplace=True)
movies2013_df['release_year'] = 2013

In [321]:
movies2013_df

link  \
Iron Man 3                         /release/rl1532659201/?ref_=bo_yld_table_1   
The Hunger Games: Catching Fire    /release/rl2638775809/?ref_=bo_yld_table_2   
Despicable Me 2                     /release/rl105874945/?ref_=bo_yld_table_3   
Man of Steel                       /release/rl4034037249/?ref_=bo_yld_table_4   
Monsters University                /release/rl1919256065/?ref_=bo_yld_table_5   
...                                                                       ...   
The East                          /release/rl995198465/?ref_=bo_yld_table_196   
Renoir                           /release/rl2808972801/?ref_=bo_yld_table_197   
The Christmas Candle             /release/rl2689304065/?ref_=bo_yld_table_198   
Krrish 3                         /release/rl3831268865/?ref_=bo_yld_table_199   
Oldboy                           /release/rl1801881089/?ref_=bo_yld_table_200   

                                theaters release_date  \
Iron Man 3                         4,253        May 3   
The Hunger Games: Catching Fire    4,163       Nov 22   
Despicable Me 2                    4,003        Jul 3   
Man of Steel                       4,207       Jun 14   
Monsters University                4,004       Jun 21   
...                                  ...          ...   
The East                             195       May 31   
Renoir                                86       Mar 29   
The Christmas Candle                 392       Nov 15   
Krrish 3                             208        Nov 1   
Oldboy                               583       Nov 27   

                                                         Distributor  \
Iron Man 3                       Walt Disney Studios Motion Pictures   
The Hunger Games: Catching Fire                            Lionsgate   
Despicable Me 2                                   Universal Pictures   
Man of Steel                                            Warner Bros.   
Monsters University              Walt Disney Studios Motion Pictures   
...                                                              ...   
The East                                    Fox Searchlight Pictures   
Renoir                                    The Samuel Goldwyn Company   
The Christmas Candle                               EchoLight Studios   
Krrish 3                                              Eros Worldwide   
Oldboy                                                  FilmDistrict   

                                 release_year  
Iron Man 3                               2013  
The Hunger Games: Catching Fire          2013  
Despicable Me 2                          2013  
Man of Steel                             2013  
Monsters University                      2013  
...                                       ...  
The East                                 2013  
Renoir                                   2013  
The Christmas Candle                     2013  
Krrish 3                                 2013  
Oldboy                                   2013  

[200 rows x 5 columns]

In [322]:
movies_page_info_list_2013 = []
for link in movies2013_df.link:
    movies_page_info_list_2013.append(get_movie_dict(link))

In [323]:
movies_page_info_list_2013

[{'movie_title': 'Iron Man 3',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 130,
  'rating': 'PG-13',
  'budget': 200000000,
  'dom_gross': 409013994,
  'int_gross': 805797258},
 {'movie_title': 'The Hunger Games: Catching Fire',
  'genres': 'Action Drama Mystery Sci-Fi Thriller',
  'runtime': 146,
  'rating': 'PG-13',
  'budget': 130000000,
  'dom_gross': 424668047,
  'int_gross': 440343699},
 {'movie_title': 'Despicable Me 2',
  'genres': 'Adventure Animation Comedy Crime Family Sci-Fi',
  'runtime': 98,
  'rating': 'PG',
  'budget': 76000000,
  'dom_gross': 368065385,
  'int_gross': 602700620},
 {'movie_title': 'Man of Steel',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 143,
  'rating': 'PG-13',
  'budget': 225000000,
  'dom_gross': 291045518,
  'int_gross': 377000000},
 {'movie_title': 'Monsters University',
  'genres': 'Adventure Animation Comedy Family Fantasy',
  'runtime': 104,
  'rating': 'G',
  'budget': None,
  'dom_gross': 268492764,
  'int_gross': 475066843}

In [324]:
movieinfo2013_df = pd.DataFrame(movies_page_info_list_2013)
movieinfo2013_df.set_index('movie_title', inplace=True)

In [325]:
movieinfo2013_df.isna().sum()

genres        0
runtime       5
rating        8
budget       63
dom_gross     0
int_gross     0
dtype: int64

In [326]:
movies2013_df = movies2013_df.merge(movieinfo2013_df, left_index=True, right_index=True)

In [327]:
movies2013_df

link  \
Iron Man 3                         /release/rl1532659201/?ref_=bo_yld_table_1   
The Hunger Games: Catching Fire    /release/rl2638775809/?ref_=bo_yld_table_2   
Despicable Me 2                     /release/rl105874945/?ref_=bo_yld_table_3   
Man of Steel                       /release/rl4034037249/?ref_=bo_yld_table_4   
Monsters University                /release/rl1919256065/?ref_=bo_yld_table_5   
...                                                                       ...   
The East                          /release/rl995198465/?ref_=bo_yld_table_196   
Renoir                           /release/rl2808972801/?ref_=bo_yld_table_197   
The Christmas Candle             /release/rl2689304065/?ref_=bo_yld_table_198   
Krrish 3                         /release/rl3831268865/?ref_=bo_yld_table_199   
Oldboy                           /release/rl1801881089/?ref_=bo_yld_table_200   

                                theaters release_date  \
Iron Man 3                         4,253        May 3   
The Hunger Games: Catching Fire    4,163       Nov 22   
Despicable Me 2                    4,003        Jul 3   
Man of Steel                       4,207       Jun 14   
Monsters University                4,004       Jun 21   
...                                  ...          ...   
The East                             195       May 31   
Renoir                                86       Mar 29   
The Christmas Candle                 392       Nov 15   
Krrish 3                             208        Nov 1   
Oldboy                               583       Nov 27   

                                                         Distributor  \
Iron Man 3                       Walt Disney Studios Motion Pictures   
The Hunger Games: Catching Fire                            Lionsgate   
Despicable Me 2                                   Universal Pictures   
Man of Steel                                            Warner Bros.   
Monsters University              Walt Disney Studios Motion Pictures   
...                                                              ...   
The East                                    Fox Searchlight Pictures   
Renoir                                    The Samuel Goldwyn Company   
The Christmas Candle                               EchoLight Studios   
Krrish 3                                              Eros Worldwide   
Oldboy                                                  FilmDistrict   

                                 release_year  \
Iron Man 3                               2013   
The Hunger Games: Catching Fire          2013   
Despicable Me 2                          2013   
Man of Steel                             2013   
Monsters University                      2013   
...                                       ...   
The East                                 2013   
Renoir                                   2013   
The Christmas Candle                     2013   
Krrish 3                                 2013   
Oldboy                                   2013   

                                                                         genres  \
Iron Man 3                                              Action Adventure Sci-Fi   
The Hunger Games: Catching Fire            Action Drama Mystery Sci-Fi Thriller   
Despicable Me 2                  Adventure Animation Comedy Crime Family Sci-Fi   
Man of Steel                                            Action Adventure Sci-Fi   
Monsters University                   Adventure Animation Comedy Family Fantasy   
...                                                                         ...   
The East                                                   Crime Drama Thriller   
Renoir                                          Biography Drama History Romance   
The Christmas Candle                                               Drama Family   
Krrish 3                                                Action Adventure Sci-Fi   
Oldboy                                          

In [328]:
movies2013_df.to_csv('movies_2013')

In [329]:
#requesting movies for 2012
url8 = 'https://www.boxofficemojo.com/year/2012/?ref_=bo_yl_table_10'
soup = url_to_soup(url8)

In [330]:
table2012 = soup.find('table')
rows = [row for row in table2012.find_all('tr')]

In [331]:
movies2012 = {}

for row in rows[1:]:
    items = row.find_all('td')
    link = items[1].find('a')
    title, url = link.text, link.get('href')
    theaters = row.find('td', class_="a-text-right mojo-field-type-positive_integer").text
    release_date = row.find('td', class_="a-text-left mojo-field-type-date a-nowrap").text
    distributor = row.find_all('td', class_="a-text-left mojo-field-type-studio")[0].text
    movies2012[title] = [url, theaters, release_date, distributor]

In [332]:
movies2012_df = pd.DataFrame(movies2012).T
movies2012_df.columns = ['link', 'theaters', 'release_date', 'Distributor']
movies2012_df['Distributor'].replace('\n', '', regex=True, inplace=True)
movies2012_df['release_year'] = 2012

In [333]:
movies2012_df

link  \
The Avengers                                  /release/rl709199361/?ref_=bo_yld_table_1   
The Dark Knight Rises                        /release/rl3745875457/?ref_=bo_yld_table_2   
The Hunger Games                             /release/rl4049110529/?ref_=bo_yld_table_3   
Skyfall                                      /release/rl1346799105/?ref_=bo_yld_table_4   
The Twilight Saga: Breaking Dawn - Part 2    /release/rl3276178945/?ref_=bo_yld_table_5   
...                                                                                 ...   
Samsara                                    /release/rl1399817729/?ref_=bo_yld_table_196   
Girl in Progress                            /release/rl441746945/?ref_=bo_yld_table_197   
Jiro Dreams of Sushi                         /release/rl39683585/?ref_=bo_yld_table_198   
Ruby Sparks                                /release/rl3496773121/?ref_=bo_yld_table_199   
Jack and Jill                              /release/rl2388297217/?ref_=bo_yld_table_200   

                                          theaters release_date  \
The Avengers                                 4,349        May 4   
The Dark Knight Rises                        4,404       Jul 20   
The Hunger Games                             4,137       Mar 23   
Skyfall                                      3,526        Nov 9   
The Twilight Saga: Breaking Dawn - Part 2    4,070       Nov 16   
...                                            ...          ...   
Samsara                                         70       Aug 24   
Girl in Progress                               322       May 11   
Jiro Dreams of Sushi                            80        Mar 9   
Ruby Sparks                                    261       Jul 25   
Jack and Jill                                3,438       Nov 11   

                                                                   Distributor  \
The Avengers                               Walt Disney Studios Motion Pictures   
The Dark Knight Rises                                             Warner Bros.   
The Hunger Games                                                     Lionsgate   
Skyfall                                      Sony Pictures Entertainment (SPE)   
The Twilight Saga: Breaking Dawn - Part 2                            Lionsgate   
...                                                                        ...   
Samsara                                                           Oscilloscope   
Girl in Progress                                                     Lionsgate   
Jiro Dreams of Sushi                                         Magnolia Pictures   
Ruby Sparks                                           Fox Searchlight Pictures   
Jack and Jill                                Sony Pictures Entertainment (SPE)   

                                           release_year  
The Avengers                                       2012  
The Dark Knight Rises                              2012  
The Hunger Games                                   2012  
Skyfall                                            2012  
The Twilight Saga: Breaking Dawn - Part 2          2012  
...                                                 ...  
Samsara                                            2012  
Girl in Progress                                   2012  
Jiro Dreams of Sushi                               2012  
Ruby Sparks                                        2012  
Jack and Jill                                      2012  

[200 rows x 5 columns]

In [334]:
movies_page_info_list_2012 = []
for link in movies2012_df.link:
    movies_page_info_list_2012.append(get_movie_dict(link))

In [335]:
movies_page_info_list_2012

[{'movie_title': 'The Avengers',
  'genres': 'Action Adventure Sci-Fi',
  'runtime': 143,
  'rating': 'PG-13',
  'budget': 220000000,
  'dom_gross': 623357910,
  'int_gross': 895455078},
 {'movie_title': 'The Dark Knight Rises',
  'genres': 'Action',
  'runtime': 164,
  'rating': 'PG-13',
  'budget': 250000000,
  'dom_gross': 448139099,
  'int_gross': 632902188},
 {'movie_title': 'The Hunger Games',
  'genres': 'Action Adventure Sci-Fi Thriller',
  'runtime': 142,
  'rating': 'PG-13',
  'budget': 78000000,
  'dom_gross': 408010692,
  'int_gross': 286384032},
 {'movie_title': 'Skyfall',
  'genres': 'Action Adventure Thriller',
  'runtime': 143,
  'rating': 'PG-13',
  'budget': 200000000,
  'dom_gross': 304360277,
  'int_gross': 804200736},
 {'movie_title': 'The Twilight Saga: Breaking Dawn',
  'genres': 'Adventure Drama Fantasy Romance',
  'runtime': 115,
  'rating': 'PG-13',
  'budget': 120000000,
  'dom_gross': 292324737,
  'int_gross': 537422083},
 {'movie_title': 'The Amazing Spider

In [336]:
movieinfo2012_df = pd.DataFrame(movies_page_info_list_2012)
movieinfo2012_df.set_index('movie_title', inplace=True)

In [337]:
movieinfo2012_df.isna().sum()

genres        0
runtime       6
rating        9
budget       79
dom_gross     0
int_gross     0
dtype: int64

In [338]:
movies2012_df = movies2012_df.merge(movieinfo2012_df, left_index=True, right_index=True)

In [339]:
movies2012_df

link  \
2016: Obama's America                 /release/rl1665238529/?ref_=bo_yld_table_100   
21 Jump Street                         /release/rl1564575233/?ref_=bo_yld_table_18   
A Dangerous Method                     /release/rl692880897/?ref_=bo_yld_table_173   
A Separation                          /release/rl2168620545/?ref_=bo_yld_table_156   
A Thousand Words                      /release/rl3846342145/?ref_=bo_yld_table_123   
...                                                                            ...   
We Bought a Zoo                        /release/rl2638644737/?ref_=bo_yld_table_88   
What to Expect When You're Expecting   /release/rl3799549441/?ref_=bo_yld_table_83   
Won't Back Down                       /release/rl3395257857/?ref_=bo_yld_table_166   
Wrath of the Titans                     /release/rl977962497/?ref_=bo_yld_table_34   
Young Adult                           /release/rl2356839937/?ref_=bo_yld_table_170   

                                     theaters release_date  \
2016: Obama's America                   2,017       Jul 13   
21 Jump Street                          3,148       Mar 16   
A Dangerous Method                        365       Nov 23   
A Separation                              282       Dec 30   
A Thousand Words                        1,895        Mar 9   
...                                       ...          ...   
We Bought a Zoo                         3,170       Dec 23   
What to Expect When You're Expecting    3,021       May 18   
Won't Back Down                         2,517       Sep 28   
Wrath of the Titans                     3,545       Mar 30   
Young Adult                               987        Dec 9   

                                                            Distributor  \
2016: Obama's America                           Rocky Mountain Pictures   
21 Jump Street                        Sony Pictures Entertainment (SPE)   
A Dangerous Method                               Sony Pictures Classics   
A Separation                                     Sony Pictures Classics   
A Thousand Words                                             DreamWorks   
...                                                                 ...   
We Bought a Zoo                                   Twentieth Century Fox   
What to Expect When You're Expecting                          Lionsgate   
Won't Back Down                                   Twentieth Century Fox   
Wrath of the Titans                                        Warner Bros.   
Young Adult                                          Paramount Pictures   

                                      release_year  \
2016: Obama's America                         2012   
21 Jump Street                                2012   
A Dangerous Method                            2012   
A Separation                                  2012   
A Thousand Words                              2012   
...                                            ...   
We Bought a Zoo                               2012   
What to Expect When You're Expecting          2012   
Won't Back Down                               2012   
Wrath of the Titans                           2012   
Young Adult                                   2012   

                                                                genres  \
2016: Obama's America                                      Documentary   
21 Jump Street                                     Action Comedy Crime   
A Dangerous Method                    Biography Drama Romance Thriller   
A Separation                                                     Drama   
A Thousand Words                                          Comedy Drama   
...                                                                ...   
We Bought a Zoo                                    Comedy Drama Family   
What to Expect When You're Expecting              Comedy Drama Romance   
Won't Back Down                                                  Drama   
Wrath of t

In [340]:
movies2012_df.to_csv('movies_2012')

In [341]:
movies2012_df.head(3)

link theaters  \
2016: Obama's America  /release/rl1665238529/?ref_=bo_yld_table_100    2,017   
21 Jump Street          /release/rl1564575233/?ref_=bo_yld_table_18    3,148   
A Dangerous Method      /release/rl692880897/?ref_=bo_yld_table_173      365   

                      release_date                        Distributor  \
2016: Obama's America       Jul 13            Rocky Mountain Pictures   
21 Jump Street              Mar 16  Sony Pictures Entertainment (SPE)   
A Dangerous Method          Nov 23             Sony Pictures Classics   

                       release_year                            genres  \
2016: Obama's America          2012                       Documentary   
21 Jump Street                 2012               Action Comedy Crime   
A Dangerous Method             2012  Biography Drama Romance Thriller   

                       runtime rating      budget  dom_gross  int_gross  
2016: Obama's America     87.0     PG         NaN   33449086   33449086  
21 Jump Street           109.0      R  42000000.0  138447667   63137661  
A Dangerous Method        99.0      R         NaN    5704709   24814727

In [342]:
movies2013_df.head(3)

link  \
Iron Man 3                       /release/rl1532659201/?ref_=bo_yld_table_1   
The Hunger Games: Catching Fire  /release/rl2638775809/?ref_=bo_yld_table_2   
Despicable Me 2                   /release/rl105874945/?ref_=bo_yld_table_3   

                                theaters release_date  \
Iron Man 3                         4,253        May 3   
The Hunger Games: Catching Fire    4,163       Nov 22   
Despicable Me 2                    4,003        Jul 3   

                                                         Distributor  \
Iron Man 3                       Walt Disney Studios Motion Pictures   
The Hunger Games: Catching Fire                            Lionsgate   
Despicable Me 2                                   Universal Pictures   

                                 release_year  \
Iron Man 3                               2013   
The Hunger Games: Catching Fire          2013   
Despicable Me 2                          2013   

                                                                         genres  \
Iron Man 3                                              Action Adventure Sci-Fi   
The Hunger Games: Catching Fire            Action Drama Mystery Sci-Fi Thriller   
Despicable Me 2                  Adventure Animation Comedy Crime Family Sci-Fi   

                                 runtime rating       budget  dom_gross  \
Iron Man 3                         130.0  PG-13  200000000.0  409013994   
The Hunger Games: Catching Fire    146.0  PG-13  130000000.0  424668047   
Despicable Me 2                     98.0     PG   76000000.0  368065385   

                                 int_gross  
Iron Man 3                       805797258  
The Hunger Games: Catching Fire  440343699  
Despicable Me 2                  602700620

In [343]:
movies2014_df.head(3)

link  \
Guardians of the Galaxy              /release/rl3177416193/?ref_=bo_yld_table_1   
Captain America: The Winter Soldier  /release/rl3194193409/?ref_=bo_yld_table_3   
The Lego Movie                        /release/rl643728897/?ref_=bo_yld_table_4   

                                    theaters release_date  \
Guardians of the Galaxy                4,088        Aug 1   
Captain America: The Winter Soldier    3,938        Apr 4   
The Lego Movie                         3,890        Feb 7   

                                                             Distributor  \
Guardians of the Galaxy              Walt Disney Studios Motion Pictures   
Captain America: The Winter Soldier  Walt Disney Studios Motion Pictures   
The Lego Movie                                              Warner Bros.   

                                     release_year  \
Guardians of the Galaxy                      2014   
Captain America: The Winter Soldier          2014   
The Lego Movie                               2014   

                                                                               genres  \
Guardians of the Galaxy                                Action Adventure Comedy Sci-Fi   
Captain America: The Winter Soldier                  Action Adventure Sci-Fi Thriller   
The Lego Movie                       Adventure Animation Comedy Family Fantasy Sci-Fi   

                                     runtime rating       budget  dom_gross  \
Guardians of the Galaxy                121.0  PG-13  170000000.0  333176600   
Captain America: The Winter Soldier    136.0  PG-13  170000000.0  259766572   
The Lego Movie                         100.0     PG   60000000.0  257760692   

                                     int_gross  
Guardians of the Galaxy              439600000  
Captain America: The Winter Soldier  454654931  
The Lego Movie                       210300000

In [344]:
movies2015_df.head(3)

link theaters  \
90 Minutes in Heaven  /release/rl2759689729/?ref_=bo_yld_table_165      899   
A Most Violent Year   /release/rl3110438401/?ref_=bo_yld_table_160      818   
A Walk in the Woods    /release/rl3547956737/?ref_=bo_yld_table_84    2,158   

                     release_date                 Distributor  release_year  \
90 Minutes in Heaven       Sep 11  The Samuel Goldwyn Company          2015   
A Most Violent Year        Dec 31                         A24          2015   
A Walk in the Woods         Sep 2        Broad Green Pictures          2015   

                                                genres  runtime rating  \
90 Minutes in Heaven                             Drama    121.0  PG-13   
A Most Violent Year        Action Crime Drama Thriller    125.0      R   
A Walk in the Woods   Adventure Biography Comedy Drama    104.0      R   

                          budget  dom_gross  int_gross  
90 Minutes in Heaven   5000000.0    4842699    4842699  
A Most Violent Year   20000000.0    5749134    6257936  
A Walk in the Woods          NaN   29504281    7956993

In [345]:
movies2016_df.head(3)

link  \
Finding Dory                  /release/rl3764946433/?ref_=bo_yld_table_1   
Rogue One: A Star Wars Story  /release/rl2557707777/?ref_=bo_yld_table_2   
Captain America: Civil War    /release/rl3210970625/?ref_=bo_yld_table_3   

                             theaters release_date  \
Finding Dory                    4,305       Jun 17   
Rogue One: A Star Wars Story    4,157       Dec 16   
Captain America: Civil War      4,226        May 6   

                                                      Distributor  \
Finding Dory                  Walt Disney Studios Motion Pictures   
Rogue One: A Star Wars Story  Walt Disney Studios Motion Pictures   
Captain America: Civil War    Walt Disney Studios Motion Pictures   

                              release_year                             genres  \
Finding Dory                          2016  Adventure Animation Comedy Family   
Rogue One: A Star Wars Story          2016            Action Adventure Sci-Fi   
Captain America: Civil War            2016            Action Adventure Sci-Fi   

                              runtime rating       budget  dom_gross  \
Finding Dory                     97.0     PG          NaN  486295561   
Rogue One: A Star Wars Story    133.0  PG-13  200000000.0  532177324   
Captain America: Civil War      147.0  PG-13  250000000.0  408084349   

                              int_gross  
Finding Dory                  542275328  
Rogue One: A Star Wars Story  523879949  
Captain America: Civil War    745211944

In [346]:
movies2017_df.head(3)

link  \
Beauty and the Beast             /release/rl222594561/?ref_=bo_yld_table_2   
Wonder Woman                     /release/rl578455041/?ref_=bo_yld_table_3   
Guardians of the Galaxy Vol. 2  /release/rl2976089601/?ref_=bo_yld_table_4   

                               theaters release_date  \
Beauty and the Beast              4,210       Mar 17   
Wonder Woman                      4,165        Jun 2   
Guardians of the Galaxy Vol. 2    4,347        May 5   

                                                        Distributor  \
Beauty and the Beast            Walt Disney Studios Motion Pictures   
Wonder Woman                                           Warner Bros.   
Guardians of the Galaxy Vol. 2  Walt Disney Studios Motion Pictures   

                                release_year  \
Beauty and the Beast                    2017   
Wonder Woman                            2017   
Guardians of the Galaxy Vol. 2          2017   

                                                             genres  runtime  \
Beauty and the Beast                 Family Fantasy Musical Romance    129.0   
Wonder Woman                    Action Adventure Fantasy Sci-Fi War    141.0   
Guardians of the Galaxy Vol. 2       Action Adventure Comedy Sci-Fi    136.0   

                               rating       budget  dom_gross  int_gross  
Beauty and the Beast               PG  160000000.0  504014165  759506961  
Wonder Woman                    PG-13  149000000.0  412563408  409283604  
Guardians of the Galaxy Vol. 2  PG-13  200000000.0  389813101  473942950

In [347]:
movies2018_df.head(3)

link theaters  \
Black Panther           /release/rl2992866817/?ref_=bo_yld_table_1    4,084   
Avengers: Infinity War  /release/rl3043198465/?ref_=bo_yld_table_2    4,474   
Incredibles 2           /release/rl2071758337/?ref_=bo_yld_table_3    4,410   

                       release_date                          Distributor  \
Black Panther                Feb 16  Walt Disney Studios Motion Pictures   
Avengers: Infinity War       Apr 27  Walt Disney Studios Motion Pictures   
Incredibles 2                Jun 15  Walt Disney Studios Motion Pictures   

                        release_year  \
Black Panther                   2018   
Avengers: Infinity War          2018   
Incredibles 2                   2018   

                                                                 genres  \
Black Panther                                   Action Adventure Sci-Fi   
Avengers: Infinity War                          Action Adventure Sci-Fi   
Incredibles 2           Action Adventure Animation Comedy Family Sci-Fi   

                        runtime rating  budget  dom_gross   int_gross  
Black Panther             134.0  PG-13     NaN  700059566   646853595  
Avengers: Infinity War    149.0  PG-13     NaN  678815482  1369544272  
Incredibles 2             118.0     PG     NaN  608581744   634223615

In [348]:
movies2019_df.head(3)

link  \
21 Bridges                            /release/rl2886174209/?ref_=bo_yld_table_86   
47 Meters Down: Uncaged              /release/rl1526892033/?ref_=bo_yld_table_100   
A Beautiful Day in the Neighborhood   /release/rl2651096577/?ref_=bo_yld_table_49   

                                    theaters release_date  \
21 Bridges                             2,665       Nov 22   
47 Meters Down: Uncaged                2,883       Aug 16   
A Beautiful Day in the Neighborhood    3,491       Nov 22   

                                                               Distributor  \
21 Bridges                                               STX Entertainment   
47 Meters Down: Uncaged              Entertainment Studios Motion Pictures   
A Beautiful Day in the Neighborhood      Sony Pictures Entertainment (SPE)   

                                     release_year  \
21 Bridges                                   2019   
47 Meters Down: Uncaged                      2019   
A Beautiful Day in the Neighborhood          2019   

                                                              genres  runtime  \
21 Bridges                                     Action Crime Thriller     99.0   
47 Meters Down: Uncaged              Adventure Drama Horror Thriller     90.0   
A Beautiful Day in the Neighborhood                  Biography Drama    109.0   

                                    rating      budget  dom_gross  int_gross  
21 Bridges                               R  33000000.0   28539757   21400000  
47 Meters Down: Uncaged              PG-13  12000000.0   22260900   25321663  
A Beautiful Day in the Neighborhood     PG  25000000.0   61704055    6056822

In [349]:
movies_main_df = pd.concat([movies2012_df, movies2013_df, movies2014_df, movies2015_df, movies2016_df, movies2017_df, movies2018_df, movies2019_df])

In [350]:
movies_main_df

link  \
2016: Obama's America       /release/rl1665238529/?ref_=bo_yld_table_100   
21 Jump Street               /release/rl1564575233/?ref_=bo_yld_table_18   
A Dangerous Method           /release/rl692880897/?ref_=bo_yld_table_173   
A Separation                /release/rl2168620545/?ref_=bo_yld_table_156   
A Thousand Words            /release/rl3846342145/?ref_=bo_yld_table_123   
...                                                                  ...   
What Men Want                /release/rl3221390849/?ref_=bo_yld_table_54   
Where'd You Go, Bernadette  /release/rl2567276033/?ref_=bo_yld_table_138   
Wonder Park                  /release/rl2575074817/?ref_=bo_yld_table_61   
Yesterday                    /release/rl1392805377/?ref_=bo_yld_table_38   
Zombieland: Double Tap        /release/rl201819649/?ref_=bo_yld_table_40   

                           theaters release_date  \
2016: Obama's America         2,017       Jul 13   
21 Jump Street                3,148       Mar 16   
A Dangerous Method              365       Nov 23   
A Separation                    282       Dec 30   
A Thousand Words              1,895        Mar 9   
...                             ...          ...   
What Men Want                 2,912        Feb 8   
Where'd You Go, Bernadette    2,404       Aug 16   
Wonder Park                   3,838       Mar 15   
Yesterday                     2,755       Jun 28   
Zombieland: Double Tap        3,468       Oct 18   

                                                  Distributor  release_year  \
2016: Obama's America                 Rocky Mountain Pictures          2012   
21 Jump Street              Sony Pictures Entertainment (SPE)          2012   
A Dangerous Method                     Sony Pictures Classics          2012   
A Separation                           Sony Pictures Classics          2012   
A Thousand Words                                   DreamWorks          2012   
...                                                       ...           ...   
What Men Want                              Paramount Pictures          2019   
Where'd You Go, Bernadette           United Artists Releasing          2019   
Wonder Park                                Paramount Pictures          2019   
Yesterday                                  Universal Pictures          2019   
Zombieland: Double Tap      Sony Pictures Entertainment (SPE)          2019   

                                                                     genres  \
2016: Obama's America                                           Documentary   
21 Jump Street                                          Action Comedy Crime   
A Dangerous Method                         Biography Drama Romance Thriller   
A Separation                                                          Drama   
A Thousand Words                                               Comedy Drama   
...                                                                     ...   
What Men Want                                        Comedy Fantasy Romance   
Where'd You Go, Bernadette                                     Comedy Drama   
Wonder Park                 Adventure Animation Comedy Drama Family Fantasy   
Yesterday                                      Comedy Fantasy Music Romance   
Zombieland: Double Tap                                 Action Comedy Horror   

                            runtime rating      budget  dom_gross  int_gross  
2016: Obama's America          87.0     PG         NaN   33449086   33449086  
21 Jump Street                109.0      R  42000000.0  138447667   63137661  
A Dangerous Method             99.0      R         NaN    5704709   24814727  
A Separation                  123.0  PG-13         NaN    7099055   15827021  
A Thousand Words               91.0  PG-13  40000000.0   18450127    3594150  
...                             ...    ...         ...        ...        ...  
What Men Want                 117.0      R  20000000.0   54611903   17604391  


In [351]:
movies_main_df.to_csv('movies_data')

In [352]:
movies_main_df.isna().sum()

link              0
theaters          0
release_date      0
Distributor       0
release_year      0
genres            0
runtime          45
rating           74
budget          602
dom_gross         0
int_gross         0
dtype: int64